# Predicting US Working Visa Applications

In [1]:
#Import the required packages
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
from matplotlib.backends.backend_pdf import PdfPages
import seaborn as sns
import itertools
from bs4 import BeautifulSoup
import urllib.request
import re
from patsy import dmatrices
from sklearn.cross_validation import train_test_split
from sklearn import metrics
from sklearn.cross_validation import cross_val_score
from sklearn.tree import export_graphviz
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
%matplotlib inline
%config IPCompleter.greedy=True
import statsmodels.formula.api as sm
from sklearn import model_selection
from sklearn.linear_model import LogisticRegression
from scipy import stats
stats.chisqprob = lambda chisq, df: stats.chi2.sf(chisq, df)

#Display all columns in tables which were being left out before
#https://stackoverflow.com/questions/11707586/python-pandas-how-to-widen-output-display-to-see-more-columns
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 154 )

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
#Reading in balanced and unbalanced dataframes from CSV
new_df_clean1 = pd.read_csv("US-Perm-Visa-PlottedFeaturesBalanced.csv")
new_df_clean_Unbal = pd.read_csv("US-Perm-Visa-PlottedFeaturesUnbalanced.csv")

In [3]:
new_df_clean1.select_dtypes(['object']).describe().T

count unique  \
case_status                  28626      2   
country_of_citizenship       26113    154   
decision_date                28626   1176   
employer_address_1           28626  11241   
employer_city                28626   2671   
employer_name                28626  11324   
employer_postal_code         28621   5363   
employer_state               28616     52   
pw_job_title_9089            19403   1592   
pw_level_9089                25622      4   
pw_soc_code                  28599    630   
pw_soc_title                 27491    420   
pw_source_name_9089          27510      6   
pw_unit_of_pay_9089          28532      5   
wage_offer_unit_of_pay_9089  17882      5   

                                                                       top  \
case_status                                                         Denied   
country_of_citizenship                                               INDIA   
decision_date                                                   2016-06-20   
employer_address_1                              2200 MISSION COLLEGE BLVD.   
employer_city                                                     NEW YORK   
employer_name                COGNIZANT TECHNOLOGY SOLUTIONS US CORPORATION   
employer_postal_code                                                 95052   
employer_state                                                  CALIFORNIA   
pw_job_title_9089                        Software Developers, Applications   
pw_level_9089                                                     Level II   
pw_soc_code                                                        15-1132   
pw_soc_title                             Software Developers, Applications   
pw_source_name_9089                                                    OES   
pw_unit_of_pay_9089                                                   Year   
wage_offer_unit_of_pay_9089                                           Year   

                              freq  
case_status                  14313  
country_of_citizenship       16208  
decision_date                  119  
employer_address_1             699  
employer_city                 1275  
employer_name                  698  
employer_postal_code           693  
employer_state                6616  
pw_job_title_9089             4725  
pw_level_9089                 9816  
pw_soc_code                   8390  
pw_soc_title                  8378  
pw_source_name_9089          25127  
pw_unit_of_pay_9089          28042  
wage_offer_unit_of_pay_9089  17628

We'll first take a look at the variables with high cardinalities and their associated values.

In [4]:
country = new_df_clean1.groupby('country_of_citizenship').size().reset_index()
country.sort_values(0, ascending=False)

country_of_citizenship      0
60                              INDIA  16208
28                              CHINA   1750
106                       PHILIPPINES    966
26                             CANADA    864
121                       SOUTH KOREA    611
88                             MEXICO    509
144                    UNITED KINGDOM    325
132                            TAIWAN    290
101                          PAKISTAN    272
94                              NEPAL    228
69                              JAPAN    200
148                         VENEZUELA    185
29                           COLOMBIA    179
46                             FRANCE    176
20                             BRAZIL    173
139                            TURKEY    167
110                            RUSSIA    138
48                            GERMANY    125
66                              ITALY    102
3                           ARGENTINA     96
65                             ISRAEL     91
145          UNITED STATES OF AMERICA     90
9                          BANGLADESH     88
142                           UKRAINE     87
62                               IRAN     87
122                             SPAIN     84
68                            JAMAICA     83
99                            NIGERIA     79
61                          INDONESIA     72
105                              PERU     72
40                              EGYPT     69
64                            IRELAND     61
85                           MALAYSIA     59
120                      SOUTH AFRICA     59
149                           VIETNAM     56
109                           ROMANIA     56
76                            LEBANON     54
5                           AUSTRALIA     54
107                            POLAND     52
117                         SINGAPORE     49
135                          THAILAND     48
72                              KENYA     45
50                             GREECE     42
123                         SRI LANKA     38
70                             JORDAN     36
39                            ECUADOR     36
21                           BULGARIA     35
96                        NEW ZEALAND     32
137               TRINIDAD AND TOBAGO     32
95                        NETHERLANDS     31
57                          HONG KONG     30
38                 DOMINICAN REPUBLIC     28
56                           HONDURAS     28
27                              CHILE     27
11                            BELARUS     27
131                             SYRIA     26
129                            SWEDEN     24
36                            DENMARK     23
49                              GHANA     20
41                        EL SALVADOR     20
153                          ZIMBABWE     18
58                            HUNGARY     16
108                          PORTUGAL     16
89                            MOLDOVA     15
93                            MOROCCO     15
4                             ARMENIA     14
12                            BELGIUM     13
115                            SERBIA     13
43                           ETHIOPIA     13
17                            BOLIVIA     12
130                       SWITZERLAND     12
147                        UZBEKISTAN     12
118                          SLOVAKIA     12
52                          GUATEMALA     11
51                            GRENADA     11
103                            PANAMA     10
34                     CZECH REPUBLIC     10
71                         KAZAKHSTAN     10
97                          NICARAGUA      9
82                          MACEDONIA      9
8                             BAHAMAS      9
100                            NORWAY      9
10                           BARBADOS      9
45                            FINLAND      8
30                         COSTA RICA      8
25                           CAMEROON      8
146                           URUGUAY      8
114                           SENEGAL      8
134       

In [5]:
country2 = new_df_clean_Unbal.groupby('country_of_citizenship').size().reset_index()
country2.sort_values(0,ascending=False)

country_of_citizenship      0
70                              INDIA  92961
33                              CHINA  11147
31                             CANADA   4622
144                       SOUTH KOREA   3057
127                       PHILIPPINES   2865
104                            MEXICO   1867
169                    UNITED KINGDOM   1561
156                            TAIWAN   1447
120                          PAKISTAN   1348
112                             NEPAL   1208
53                             FRANCE   1058
163                            TURKEY    948
23                             BRAZIL    855
79                              JAPAN    844
131                            RUSSIA    833
57                            GERMANY    750
174                         VENEZUELA    733
34                           COLOMBIA    626
76                              ITALY    539
167                           UKRAINE    517
75                             ISRAEL    508
117                           NIGERIA    480
72                               IRAN    476
146                             SPAIN    473
12                         BANGLADESH    404
5                           ARGENTINA    384
99                           MALAYSIA    360
45                              EGYPT    348
130                           ROMANIA    328
175                           VIETNAM    327
71                          INDONESIA    312
74                            IRELAND    310
7                           AUSTRALIA    299
140                         SINGAPORE    290
126                              PERU    267
128                            POLAND    258
143                      SOUTH AFRICA    247
170          UNITED STATES OF AMERICA    242
89                            LEBANON    241
25                           BULGARIA    240
147                         SRI LANKA    234
80                             JORDAN    233
159                          THAILAND    227
78                            JAMAICA    220
59                             GREECE    219
67                          HONG KONG    211
82                              KENYA    192
58                              GHANA    156
113                       NETHERLANDS    152
114                       NEW ZEALAND    152
153                            SWEDEN    147
161               TRINIDAD AND TOBAGO    141
44                            ECUADOR    136
32                              CHILE    135
155                             SYRIA    132
14                            BELARUS    130
43                 DOMINICAN REPUBLIC    107
129                          PORTUGAL     95
68                            HUNGARY     94
137                            SERBIA     94
66                           HONDURAS     90
154                       SWITZERLAND     81
179                          ZIMBABWE     80
50                           ETHIOPIA     77
41                            DENMARK     74
15                            BELGIUM     71
109                           MOROCCO     67
46                        EL SALVADOR     66
35                         COSTA RICA     65
20                            BOLIVIA     59
8                             AUSTRIA     56
39                     CZECH REPUBLIC     55
6                             ARMENIA     54
10                            BAHAMAS     49
81                         KAZAKHSTAN     48
172                        UZBEKISTAN     48
52                            FINLAND     45
37                            CROATIA     45
171                           URUGUAY     44
61                          GUATEMALA     43
92                              LIBYA     43
105                           MOLDOVA     43
123                            PANAMA     43
1                             ALBANIA     40
118                            NORWAY     39
30                           CAMEROON     39
158                          TANZANIA     35
56                            GEORGIA     35
60        

In [6]:
employer = new_df_clean1.groupby('employer_name').size().reset_index()
employer.sort_values(0, ascending=False)

employer_name    0
2154       COGNIZANT TECHNOLOGY SOLUTIONS US CORPORATION  698
5009                                   INTEL CORPORATION  696
4902                        INFOSYS TECHNOLOGIES LIMITED  428
4144                                         GOOGLE INC.  270
6418                               MICROSOFT CORPORATION  243
7273                                ORACLE AMERICA, INC.  185
512                                 AMAZON CORPORATE LLC  182
2629                  DALLAS INDEPENDENT SCHOOL DISTRICT  157
2030                                 CISCO SYSTEMS, INC.  147
4712                                     IBM CORPORATION  147
1157                 BALTIMORE CITY PUBLIC SCHOOL SYSTEM  144
732                                           APPLE INC.  141
4900                                        INFOSYS LTD.  125
2844                               DGN TECHNOLOGIES INC.  107
3533                                      FACEBOOK, INC.   99
1725               CAPGEMINI FINANCIAL SERVICES USA INC.   95
3372                              ERNST & YOUNG U.S. LLP   92
2757                             DELOITTE CONSULTING LLP   91
5379                                JP MORGAN CHASE & CO   89
5517                                         KFORCE INC.   88
7936                          QUALCOMM TECHNOLOGIES INC.   86
11021                                      WIPRO LIMITED   86
2237                      COMPUNNEL SOFTWARE GROUP, INC.   85
4394                                    HCL AMERICA INC.   78
1382                                      BLOOMBERG L.P.   72
11169                                        YAHOO! INC.   72
7719               PRINCE GEORGE'S COUNTY PUBLIC SCHOOLS   67
4129                                GOLDMAN, SACHS & CO.   67
3917                 GARLAND INDEPENDENT SCHOOL DISTRICT   64
31                                      3I INFOTECH INC.   62
4062                                 GLOBAL INFOTECH INC   60
10767                                       VMWARE, INC.   59
1506                                BROADCOM CORPORATION   58
6174     MASTECH, INC., A MASTECH HOLDINGS, INC. COMPANY   58
3122                                           EBAY INC.   57
8040                           RANDSTAD TECHNOLOGIES, LP   56
4395                              HCL GLOBAL SYSTEMS INC   56
4762                            IGATE TECHNOLOGIES, INC.   52
4610                           HTC GLOBAL SERVICES, INC.   52
7937                                      QUALCOMM, INC.   52
8450                                      SALESFORCE.COM   51
6586                                 MPHASIS CORPORATION   51
4469                             HEWLETT-PACKARD COMPANY   50
1169                                     BANK OF AMERICA   50
2488                                        CUMMINS INC.   50
1726                                  CAPGEMINI U.S. LLC   47
10654               VERINON TECHNOLOGY SOLUTIONS LIMITED   47
5195                                       ITECH US INC.   47
7703                              PRICEWATERHOUSECOOPERS   47
7457                                        PAYPAL, INC.   47
10848                          WAL-MART ASSOCIATES, INC.   46
3740              FORT WORTH INDEPENDENT SCHOOL DISTRICT   45
3250                                     EMC CORPORATION   45
5846                                LINKEDIN CORPORATION   45
3351                            EPIC SYSTEMS CORPORATION   44
3366                                       ERICSSON INC.   43
7075                                  NVIDIA CORPORATION   42
6414                             MICRON TECHNOLOGY, INC.   40
8569                              SAVVY INFO SYSTEMS INC   39
2459                            CSC COVANSYS CORPORATION   39
10663  VERIZON COMMUNICATIONS INC., & ALL ITS SUBSIDI...   38
233                           ADOBE SYSTEMS INCORPORATED   38
1738                           CAPITAL ONE SERVICES, LLC   38
9774                      TEXAS INSTRUMENTS INCORPORATED   38
4589         

In [7]:
employer2 = new_df_clean_Unbal.groupby('employer_name').size().reset_index()
employer2.sort_values(0, ascending=False)

employer_name     0
6055       COGNIZANT TECHNOLOGY SOLUTIONS US CORPORATION  5248
14209                                  INTEL CORPORATION  2816
11705                                        GOOGLE INC.  2394
18199                              MICROSOFT CORPORATION  1832
1371                                AMAZON CORPORATE LLC  1493
1932                                          APPLE INC.  1355
20770                               ORACLE AMERICA, INC.  1273
13946                                       INFOSYS LTD.  1128
7781                             DELOITTE CONSULTING LLP   864
5752                                 CISCO SYSTEMS, INC.   814
9985                                      FACEBOOK, INC.   799
22853                         QUALCOMM TECHNOLOGIES INC.   714
9481                              ERNST & YOUNG U.S. LLP   681
12524                                   HCL AMERICA INC.   608
15254                               JP MORGAN CHASE & CO   601
13472                                    IBM CORPORATION   546
13607                           IGATE TECHNOLOGIES, INC.   538
23156                          RANDSTAD TECHNOLOGIES, LP   501
8790                                           EBAY INC.   480
15673                                        KFORCE INC.   456
3887                                      BLOOMBERG L.P.   450
24352                                     SALESFORCE.COM   435
13949                       INFOSYS TECHNOLOGIES LIMITED   434
30513                                       VMWARE, INC.   430
4942               CAPGEMINI FINANCIAL SERVICES USA INC.   420
31656                                        YAHOO! INC.   406
6884                                        CUMMINS INC.   392
17548    MASTECH, INC., A MASTECH HOLDINGS, INC. COMPANY   375
16624                               LINKEDIN CORPORATION   375
3296                                     BANK OF AMERICA   373
4959                           CAPITAL ONE SERVICES, LLC   361
22101                             PRICEWATERHOUSECOOPERS   354
9137                                     EMC CORPORATION   352
20182                                 NVIDIA CORPORATION   347
30758                          WAL-MART ASSOCIATES, INC.   327
4251                                BROADCOM CORPORATION   323
9469                                       ERICSSON INC.   313
21342                                       PAYPAL, INC.   300
18707                                MPHASIS CORPORATION   296
30234  VERIZON COMMUNICATIONS INC., & ALL ITS SUBSIDI...   294
9419                            EPIC SYSTEMS CORPORATION   283
16276                   LARSEN & TOUBRO INFOTECH LIMITED   281
6274                      COMPUNNEL SOFTWARE GROUP, INC.   272
7780                               DELOITTE & TOUCHE LLP   268
3268                 BALTIMORE CITY PUBLIC SCHOOL SYSTEM   250
11664                                GOLDMAN SACHS & CO.   246
13108                          HTC GLOBAL SERVICES, INC.   245
7474                  DALLAS INDEPENDENT SCHOOL DISTRICT   244
5366                                  CERNER CORPORATION   238
31218                                      WIPRO LIMITED   231
10444                                            FMR LLC   228
15922                                           KPMG LLP   227
614                           ADOBE SYSTEMS INCORPORATED   224
20134                                      NTT DATA, INC   219
27782                     TEXAS INSTRUMENTS INCORPORATED   218
29974                      V-SOFT CONSULTING GROUP, INC.   214
14427                                             INTUIT   210
12727                            HEWLETT-PACKARD COMPANY   205
6814                            CSC COVANSYS CORPORATION   202
22854                                     QUALCOMM, INC.   195
22844                             QUALCOMM ATHEROS, INC.   194
18616                           MORGAN STANLEY & CO. LLC   193
7983                               DGN TECHNOLOGIES INC.   192
1476       

In [8]:
state = new_df_clean1.groupby('employer_state').size().reset_index()
state.sort_values(0, ascending=False)

employer_state     0
4             CALIFORNIA  6616
44                 TEXAS  3693
30            NEW JERSEY  2706
32              NEW YORK  2067
13              ILLINOIS  1500
22              MICHIGAN  1054
47              VIRGINIA   984
9                FLORIDA   933
21         MASSACHUSETTS   907
38          PENNSYLVANIA   875
10               GEORGIA   814
48            WASHINGTON   775
20              MARYLAND   637
33        NORTH CAROLINA   563
35                  OHIO   444
6            CONNECTICUT   322
2                ARIZONA   291
25              MISSOURI   257
5               COLORADO   236
50             WISCONSIN   230
14               INDIANA   222
23             MINNESOTA   217
42             TENNESSEE   167
16                KANSAS   153
8   DISTRICT OF COLUMBIA   142
18             LOUISIANA   134
17              KENTUCKY   128
15                  IOWA   110
3               ARKANSAS   109
43           TERRITORIES   104
27              NEBRASKA   104
31            NEW MEXICO   102
40        SOUTH CAROLINA   101
45                  UTAH   100
7               DELAWARE    98
36              OKLAHOMA    85
37                OREGON    84
0                ALABAMA    83
39          RHODE ISLAND    73
28                NEVADA    60
46               VERMONT    59
12                 IDAHO    53
29         NEW HAMPSHIRE    45
24           MISSISSIPPI    32
34          NORTH DAKOTA    30
19                 MAINE    26
41          SOUTH DAKOTA    22
11                HAWAII    20
49         WEST VIRGINIA    19
26               MONTANA    12
1                 ALASKA     9
51               WYOMING     9

In [9]:
state2 = new_df_clean_Unbal.groupby('employer_state').size().reset_index()
state2.sort_values(0, ascending=False)

employer_state      0
5             CALIFORNIA  38389
45                 TEXAS  18362
31            NEW JERSEY  13432
33              NEW YORK  11943
14              ILLINOIS   7400
22         MASSACHUSETTS   6070
49            WASHINGTON   5574
23              MICHIGAN   5554
39          PENNSYLVANIA   5113
48              VIRGINIA   4736
10               FLORIDA   4255
11               GEORGIA   4046
34        NORTH CAROLINA   2848
36                  OHIO   2505
21              MARYLAND   2366
7            CONNECTICUT   1633
26              MISSOURI   1562
2                ARIZONA   1446
51             WISCONSIN   1434
15               INDIANA   1393
24             MINNESOTA   1357
6               COLORADO   1135
43             TENNESSEE    969
18              KENTUCKY    757
17                KANSAS    690
16                  IOWA    681
9   DISTRICT OF COLUMBIA    622
3               ARKANSAS    620
28              NEBRASKA    540
8               DELAWARE    527
0                ALABAMA    495
46                  UTAH    479
19             LOUISIANA    473
38                OREGON    416
40          RHODE ISLAND    406
41        SOUTH CAROLINA    388
37              OKLAHOMA    364
32            NEW MEXICO    335
30         NEW HAMPSHIRE    304
29                NEVADA    287
44           TERRITORIES    266
47               VERMONT    247
13                 IDAHO    227
35          NORTH DAKOTA    177
42          SOUTH DAKOTA    151
20                 MAINE    138
25           MISSISSIPPI    134
50         WEST VIRGINIA    120
12                HAWAII     95
27               MONTANA     58
52               WYOMING     48
1                 ALASKA     43
4       BRITISH COLUMBIA      3

In [10]:
pw_job = new_df_clean1.groupby('pw_job_title_9089').size().reset_index()
pw_job.sort_values(0, ascending=False)

pw_job_title_9089     0
1355                  Software Developers, Applications  4725
332                           Computer Systems Analysts  1903
311           Computer Software Engineers, Applications   834
1370              Software Developers, Systems Software   731
476              Electronics Engineers, Except Computer   709
350           Computer and Information Systems Managers   543
26                             Accountants and Auditors   277
490   Elementary School Teachers, Except Special Edu...   259
316       Computer Software Engineers, Systems Software   241
386                             Database Administrators   230
283                                Computer Programmers   223
877                                Mechanical Engineers   216
331                            Computer Systems Analyst   203
549                                  Financial Analysts   191
832                                 Management Analysts   188
962        Network and Computer Systems Administrators*   175
854                                  Marketing Managers   175
733                                 Internists, General   164
462                                Electrical Engineers   143
554                                  Financial Managers   138
961         Network and Computer Systems Administrators   135
690                                Industrial Engineers   134
1469                                      Statisticians   133
859                                 Materials Engineers   130
226                                     Civil Engineers   127
997                        Operations Research Analysts   102
1238                                    Sales Engineers   101
1267  Secondary School Teachers, Except Special and ...    98
72               Architectural and Engineering Managers    86
1431       Special Education Teachers, Secondary School    86
1347                   Software Developer, Applications    86
1061                 Physicians and Surgeons, All Other    80
989                             Occupational Therapists    76
703   Information Security Analysts, Web Developers,...    65
850   Market Research Analysts and Marketing Special...    64
919   Middle School Teachers, Except Special and Car...    63
1047                                        Pharmacists    62
1379                                  Software Engineer    59
1242                                     Sales Managers    55
891       Medical and Clinical Laboratory Technologists    55
712                          Instructional Coordinators    51
1583                  software developers, applications    50
303            Computer Software Engineer, Applications    49
25                                          Accountants    48
603                     General and Operations Managers    48
1204                  SOFTWARE DEVELOPERS, APPLICATIONS    46
616                                   Graphic Designers    46
207                                  Chemical Engineers    45
298                          Computer Software Engineer    44
169                    Business Teachers, Postsecondary    43
213                                            Chemists    43
761                                             Lawyers    41
845                            Market Research Analysts    39
849   Market Research Analysts and Marketing Special...    39
893                Medical and Health Services Managers    38
784                                        Logisticians    38
1428  Special Education Teachers, Preschool, Kinderg...    38
1269  Secondary School Teachers, Except Special and ...    37
1097                                 Programmer Analyst    37
83                                  Assistant Professor    36
268                         Computer Hardware Engineers    34
503                 Engineering Teachers, Postsecondary    34
1487                                    Systems Analyst    33
1560           computer and information systems manager    32
693     

In [11]:
pw_soc = new_df_clean1.groupby('pw_soc_title').size().reset_index()
pw_soc.sort_values(0, ascending=False)

pw_soc_title     0
373                  Software Developers, Applications  8378
94                           Computer Systems Analysts  2959
376              Software Developers, Systems Software  1325
143             Electronics Engineers, Except Computer  1035
87           Computer Software Engineers, Applications   984
101          Computer and Information Systems Managers   790
1                             Accountants and Auditors   499
145  Elementary School Teachers, Except Special Edu...   432
292       Network and Computer Systems Administrators*   429
267                               Mechanical Engineers   406
115                            Database Administrators   357
83                                Computer Programmers   335
251                                Management Analysts   316
168                                 Financial Analysts   311
258                                 Marketing Managers   304
234                                Internists, General   298
138                               Electrical Engineers   275
389                                      Statisticians   253
170                                 Financial Managers   242
89       Computer Software Engineers, Systems Software   239
257  Market Research Analysts and Marketing Special...   235
359  Secondary School Teachers, Except Special and ...   233
225                               Industrial Engineers   221
62                                     Civil Engineers   205
260                                Materials Engineers   183
352                                    Sales Engineers   172
320                 Physicians and Surgeons, All Other   168
80                     Computer Occupations, All Other   155
22              Architectural and Engineering Managers   148
281  Middle School Teachers, Except Special and Car...   144
301                            Occupational Therapists   139
302                       Operations Research Analysts   134
387       Special Education Teachers, Secondary School   126
273      Medical and Clinical Laboratory Technologists   108
315                                        Pharmacists   107
197                    General and Operations Managers   100
48                    Business Teachers, Postsecondary    90
57                                            Chemists    87
291        Network and Computer Systems Administrators    83
230  Information Security Analysts, Web Developers,...    81
118                                  Dentists, General    80
353                                     Sales Managers    79
204                                  Graphic Designers    75
231                         Instructional Coordinators    74
54                                  Chemical Engineers    72
242                                            Lawyers    72
148                Engineering Teachers, Postsecondary    69
274               Medical and Health Services Managers    67
250                                       Logisticians    66
227                     Industrial Production Managers    63
406  Transportation, Storage, and Distribution Mana...    60
360  Secondary School Teachers, Except Special and ...    60
388                       Speech-Language Pathologists    59
386  Special Education Teachers, Preschool, Kinderg...    58
19              Architects, Except Landscape and Naval    58
256                           Market Research Analysts    56
263       Mathematical Science Teachers, Postsecondary    54
43                                Biomedical Engineers    54
0                                          Accountants    52
58                                    Chief Executives    50
127                                         Economists    50
208         Health Specialties Teachers, Postsecondary    49
194  Foreign Language and Literature Teachers, Post...    49
76                         Computer Hardware Engineers    48
85            Computer Science Teachers, Postsecondary    47
39              

In [12]:
pw_soc2 = new_df_clean_Unbal.groupby('pw_soc_title').size().reset_index()
pw_soc2.sort_values(0, ascending=False)

pw_soc_title      0
481                  Software Developers, Applications  53310
120                          Computer Systems Analysts  16223
484              Software Developers, Systems Software   9641
182             Electronics Engineers, Except Computer   5652
127          Computer and Information Systems Managers   4119
113          Computer Software Engineers, Applications   3415
378       Network and Computer Systems Administrators*   2541
1                             Accountants and Auditors   2403
341                               Mechanical Engineers   2328
295                                Internists, General   2232
145                            Database Administrators   1978
213                                 Financial Analysts   1946
330                                 Marketing Managers   1793
497                                      Statisticians   1787
171                               Electrical Engineers   1709
323                                Management Analysts   1696
284                               Industrial Engineers   1288
215                                 Financial Managers   1224
104                    Computer Occupations, All Other   1221
108                               Computer Programmers   1196
329  Market Research Analysts and Marketing Special...   1187
332                                Materials Engineers   1048
415                 Physicians and Surgeons, All Other   1022
455                                    Sales Engineers    990
82                                     Civil Engineers    905
187  Elementary School Teachers, Except Special Edu...    860
31              Architectural and Engineering Managers    855
115      Computer Software Engineers, Systems Software    807
392                       Operations Research Analysts    688
64                    Business Teachers, Postsecondary    675
462  Secondary School Teachers, Except Special and ...    573
191                Engineering Teachers, Postsecondary    497
75                                            Chemists    480
409                                        Pharmacists    470
353      Medical and Clinical Laboratory Technologists    450
306                                            Lawyers    434
520  Transportation, Storage, and Distribution Mana...    424
389                            Occupational Therapists    422
250                    General and Operations Managers    408
289  Information Security Analysts, Web Developers,...    397
72                                  Chemical Engineers    383
318                                       Logisticians    382
150                                  Dentists, General    376
52                       Biochemists and Biophysicists    370
335       Mathematical Science Teachers, Postsecondary    354
264         Health Specialties Teachers, Postsecondary    354
456                                     Sales Managers    354
56                                Biomedical Engineers    350
28              Architects, Except Landscape and Naval    332
260                                  Graphic Designers    308
286                     Industrial Production Managers    296
244  Foreign Language and Literature Teachers, Post...    292
291                         Instructional Coordinators    288
288                      Information Security Analysts    283
205                   Family and General Practitioners    282
465  Securities, Commodities, and Financial Service...    281
159                                         Economists    274
377        Network and Computer Systems Administrators    272
495       Special Education Teachers, Secondary School    268
363  Middle School Teachers, Except Special and Car...    266
111           Computer Science Teachers, Postsecondary    265
354               Medical and Health Services Managers    263
101                        Computer Network Architects    260
158                  Economics Teachers, Postsecondary    254
482  Softwar

Firstly, to deal with country_of_citizenship, we decided to find a meaningful way of grouping countries, that would render itself appropriate for modelling later on. We considered grouping by continent but we felt that this was not appropriate as this kind of grouping does not take into account factors like the socio-economic status of the country, and it's relationship with the US. We decided to try and group countries in two ways and investigate which might have more predictive power. Firstly, we decided on obtaining the GDP for each country in US dollars (as categorized by the International Monetary Fund(IMF)) and creating a new column with this values. We could then group countries by GDP and us this as a means of categorizing countries in socio-economic terms. Also GDP would provide us with a continuous feature which we could also plot against case status. We considered capturing a country's relationship with the US or the way the US perceives said countries. To measure this in a meaningful and sensible way, we used the US government's travel advisory webpage, which offers one of four categories of advice (Exercise normal precautions, exercise increased caution, reconsider travel, or do not travel) for each country. We decided to use this to additionally group countries and resolve our high cardinality issue.

We scraped the GDP information from wikipedia, created a dataframe with values from this source and then merged the dataframe to add the new columns to the original dataframe for GDP.

In [13]:
# https://www.analyticsvidhya.com/blog/2015/10/beginner-guide-web-scraping-beautiful-soup-python/
url =('https://en.wikipedia.org/wiki/List_of_countries_by_GDP_(nominal)_per_capita')
gdp = urllib.request.urlopen(url)

In [14]:
soup = BeautifulSoup(gdp)
soup.prettify()

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("html5lib"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "html5lib")

  markup_type=markup_type))


'<!DOCTYPE html>\n<html class="client-nojs" dir="ltr" lang="en">\n <head>\n  <meta charset="utf-8"/>\n  <title>\n   List of countries by GDP (nominal) per capita - Wikipedia\n  </title>\n  <script>\n   document.documentElement.className = document.documentElement.className.replace( /(^|\\s)client-nojs(\\s|$)/, "$1client-js$2" );\n  </script>\n  <script>\n   (window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"List_of_countries_by_GDP_(nominal)_per_capita","wgTitle":"List of countries by GDP (nominal) per capita","wgCurRevisionId":838658647,"wgRevisionId":838658647,"wgArticleId":1050736,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Wikipedia pending changes protected pages","Lists of countries by GDP per capita"],"wgBreakFrames":false,"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgSeparatorTransformTab

In [15]:
tables=soup.find_all('table')

In [16]:
gdp_table=soup.find('table', class_='wikitable sortable')

In [17]:
print (gdp_table)

<table class="wikitable sortable" style="margin-left:auto;margin-right:auto;text-align: right">
<tbody><tr>
<th data-sort-type="number">Rank</th>
<th>Country</th>
<th><a href="/wiki/United_States_dollar" title="United States dollar">US$</a></th>
</tr>
<tr>
<td>1</td>
<td align="left"><span class="flagicon"><img alt="" class="thumbborder" data-file-height="600" data-file-width="1000" height="14" src="//upload.wikimedia.org/wikipedia/commons/thumb/d/da/Flag_of_Luxembourg.svg/23px-Flag_of_Luxembourg.svg.png" srcset="//upload.wikimedia.org/wikipedia/commons/thumb/d/da/Flag_of_Luxembourg.svg/35px-Flag_of_Luxembourg.svg.png 1.5x, //upload.wikimedia.org/wikipedia/commons/thumb/d/da/Flag_of_Luxembourg.svg/46px-Flag_of_Luxembourg.svg.png 2x" width="23"/> </span><a href="/wiki/Luxembourg" title="Luxembourg">Luxembourg</a></td>
<td>105,803</td>
</tr>
<tr>
<td>2</td>
<td align="left"><span class="flagicon"><img alt="" class="thumbborder" data-file-height="1000" data-file-width="1000" height="16" s

In [18]:
rank=[]
country=[]
gdp=[]

for row in gdp_table.findAll("tr"):
    cells = row.findAll('td')
    links = row.findAll('a')
 
    if len(cells)==3: 
        rank.append(cells[0].find(text=True))
        country.append(links[0].find(text=True))
        gdp.append(cells[2].find(text=True))

In [19]:
gdp_df=pd.DataFrame(columns=['Number'])

gdp_df['Rank']=rank
gdp_df['country']=country
gdp_df['GDP']=gdp
gdp_df['country_of_citizenship'] = gdp_df['country'].str.upper()
gdp_df1 = gdp_df.drop(['Number', 'country'], axis=1)

In [20]:
gdp_df1

Rank      GDP            country_of_citizenship
0      1  105,803                        LUXEMBOURG
1      2   80,591                       SWITZERLAND
2      —   77,451                             MACAU
3      3   74,941                            NORWAY
4      4   70,638                           IRELAND
5      5   70,332                           ICELAND
6      6   60,804                             QATAR
7      7   59,501                     UNITED STATES
8      8   57,713                         SINGAPORE
9      9   56,444                           DENMARK
10    10   55,707                         AUSTRALIA
11    11   53,218                            SWEDEN
12    12   48,346                       NETHERLANDS
13    13   47,406                        SAN MARINO
14    14   47,290                           AUSTRIA
15     —   46,109                         HONG KONG
16    15   46,017                           FINLAND
17    16   45,077                            CANADA
18    17   44,550                           GERMANY
19    18   43,582                           BELGIUM
20    19   41,593                       NEW ZEALAND
21    20   40,258                            ISRAEL
22    21   39,869                            FRANCE
23    22   39,735                    UNITED KINGDOM
24    23   38,440                             JAPAN
25    24   37,226              UNITED ARAB EMIRATES
26    25   31,984                             ITALY
27    26   31,255                           BAHAMAS
28     —   30,488                       PUERTO RICO
29    27   29,891                       SOUTH KOREA
30    28   29,712                            BRUNEI
31    29   28,359                             SPAIN
32    30   27,319                            KUWAIT
33    31   27,250                             MALTA
34    32   24,976                            CYPRUS
35     —   24,577                            TAIWAN
36    33   24,029                           BAHRAIN
37    34   23,654                          SLOVENIA
38    35   21,161                          PORTUGAL
39    36   21,120                      SAUDI ARABIA
40    37   20,152                    CZECH REPUBLIC
41    38   19,840                           ESTONIA
42    39   18,637                            GREECE
43    40   17,973                              OMAN
44    41   17,859                          BARBADOS
45    42   17,664                          SLOVAKIA
46    43   17,096                             PALAU
47    44   16,730                         LITHUANIA
48    45   16,722                           URUGUAY
49    46   16,702               ANTIGUA AND BARBUDA
50    47   16,296             SAINT KITTS AND NEVIS
51    48   15,769               TRINIDAD AND TOBAGO
52    49   15,686                        SEYCHELLES
53    50   15,547                            LATVIA
54    51   15,531                           HUNGARY
55    52   15,089                            PANAMA
56    53   15,070                             CHILE
57    54   14,467                         ARGENTINA
58    55   13,823                            POLAND
59    56   13,138                           CROATIA
60    57   12,727                 EQUATORIAL GUINEA
61    58   12,527                          MALDIVES
62    59   11,685                        COSTA RICA
63    60   11,409                           LEBANON
64    61   10,757                           ROMANIA
65     —   10,728                             WORLD
66    62   10,608                            RUSSIA
67    63   10,512                            TURKEY
68    64   10,360                           GRENADA
69    65    9,895                            BRAZIL
70    66    9,813                          MALAYSIA
71    67    9,794                         MAURITIUS
72    68    9,607                       SAINT LUCIA
73    69    9,304                            MEXICO
74    70    8,841                        KAZAKHSTAN
75    71    8,643                             CHINA


In [21]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_gdp = pd.merge(left=new_df_clean1,right=gdp_df1, how='left', left_on='country_of_citizenship', right_on='country_of_citizenship')

In [22]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_gdp2 = pd.merge(left=new_df_clean_Unbal,right=gdp_df1, how='left', left_on='country_of_citizenship', right_on='country_of_citizenship')

In [23]:
merged_gdp.head(10)

case_status country_of_citizenship decision_date         employer_address_1  \
0      Denied                  INDIA    2015-05-15         9142 MOREHEAD ROAD   
1      Denied                  INDIA    2013-02-27          ONE MICROSOFT WAY   
2   Certified               PORTUGAL    2014-08-04           699 BOYLSTON ST.   
3      Denied                  INDIA    2016-10-17       672 WEST 11TH STREET   
4   Certified                  INDIA    2016-06-17            440 TERRY AVE N   
5      Denied                GRENADA    2015-06-23          501 SOUTH JUPITER   
6   Certified                 CANADA    2015-09-02              PO BOX 244023   
7      Denied            SOUTH KOREA    2015-01-15           500 WOODLAND AVE   
8   Certified                    NaN    2012-03-29  2821 MISSION COLLEGE BLVD   
9      Denied                  INDIA    2013-05-28         9555 LEBANON ROAD.   

  employer_city                        employer_name employer_postal_code  \
0  FLEMINGSBURG              FLEMING REGIONAL CLINIC                41041   
1       REDMOND                MICROSOFT CORPORATION                98052   
2        BOSTON           CORNERSTONE RESEARCH, INC.                 2116   
3         TRACY                           AKVARR INC                95377   
4       SEATTLE                 AMAZON CORPORATE LLC                98109   
5       GARLAND  GARLAND INDEPENDENT SCHOOL DISTRICT                75042   
6    MONTGOMERY      AUBURN UNIVERSITY AT MONTGOMERY           36124-4023   
7   KANSAS CITY        DELLA LAMB COMMUNITY SERVICES                64106   
8   SANTA CLARA                          MCAFEE INC.              95054.0   
9        FRISCO                  NETWORK OBJECTS INC                75035   

  employer_state                                  pw_job_title_9089  \
0       KENTUCKY                                       Veterinarian   
1     WASHINGTON                  Software Developers, Applications   
2  MASSACHUSETTS                                         Economists   
3     CALIFORNIA                                                NaN   
4     WASHINGTON                                                NaN   
5          TEXAS  Secondary School Teachers, Except Special and ...   
6        ALABAMA                                         Economists   
7       MISSOURI  Adult Literacy, Remedial Education and GED Tea...   
8     CALIFORNIA           Computer and Information Systems Mangers   
9          TEXAS                          Computer Systems Analysts   

  pw_level_9089 pw_soc_code  \
0      Level IV     29-1131   
1      Level II     15-1132   
2     Level III     19-3011   
3      Level IV     15-1132   
4     Level III     11-3071   
5       Level I     25-2031   
6     Level III     19-3011   
7       Level I  25-3011.00   
8           NaN  11-3021.00   
9      Level II     15-1121   

                                        pw_soc_title pw_source_name_9089  \
0                                      Veterinarians                 OES   
1                  Software Developers, Applications                 OES   
2                                         Economists                 OES   
3                  Software Developers, Applications                 OES   
4  Transportation, Storage, and Distribution Mana...                 OES   
5  Secondary School Teachers, Except Special and ...                 OES   
6                                         Economists                 OES   
7  Adult Literacy, Remedial Education, and GED Te...                 OES   
8          Computer and Information Systems Managers               Other   
9                          Computer Systems Analysts                 OES   

  pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
0                Year                        Year                 0  139   
1                Year                         NaN                 0  139   
2                Year                         NaN                 1   35 

In [24]:
# Must change GDP to numerical value
merged_gdp['GDP'] = merged_gdp.GDP.str.replace(',', '').astype(float, errors='ignore')
merged_gdp2['GDP'] = merged_gdp2.GDP.str.replace(',', '').astype(float, errors='ignore')

In [25]:
merged_gdp.dtypes

case_status                     object
country_of_citizenship          object
decision_date                   object
employer_address_1              object
employer_city                   object
employer_name                   object
employer_postal_code            object
employer_state                  object
pw_job_title_9089               object
pw_level_9089                   object
pw_soc_code                     object
pw_soc_title                    object
pw_source_name_9089             object
pw_unit_of_pay_9089             object
wage_offer_unit_of_pay_9089     object
case_status_code                 int64
Rank                            object
GDP                            float64
dtype: object

Now we will group countries into low, medium and high categories, based on their GDP.

In [26]:
merged_gdp['GDP'].describe().T

count     25963.000000
mean       7859.875091
std       12756.979408
min         312.000000
25%        1983.000000
50%        1983.000000
75%        8643.000000
max      105803.000000
Name: GDP, dtype: float64

In [27]:
#Creating bins based on descriptive statistics
bins = [0, 1983, 8643, 105803]

groupNames = ['Low Rank GDP', 'Mid Rank GDP', 'High Rank GDP']
array = merged_gdp['GDP']
merged_gdp['GDPGroups']= pd.cut(array, bins=bins, labels=groupNames)
#Creating bins based on descriptive statistics
bins = [0, 1983, 8643, 105803]

array = merged_gdp2['GDP']
merged_gdp2['GDPGroups']= pd.cut(array, bins=bins, labels=groupNames)

Next, we turned to categorizing countries according to travel advice issued by the US government. 

In [28]:
# https://www.analyticsvidhya.com/blog/2015/10/beginner-guide-web-scraping-beautiful-soup-python/
url =('https://travel.state.gov/content/travel/en/traveladvisories/traveladvisories.html')
travel_advice = urllib.request.urlopen(url)

In [29]:
soup = BeautifulSoup(travel_advice)
soup.prettify()

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("html5lib"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "html5lib")

  markup_type=markup_type))


'<!-- START CAPTCHA -->\n<html>\n <head>\n  <script async="" defer="" src="//www.google.com/recaptcha/api.js?onload=onloadCallback&amp;render=explicit" type="text/javascript">\n  </script>\n  <script type="text/javascript">\n   var onloadCallback = function() {\n           \tif ($(\'#captchaImage\').length) { \n               \t\tgrecaptcha.render(\'captchaImage\', {\n               \t\t\t\'sitekey\' : \'6Ld0yEcUAAAAAHz2KIeCdmJjT01qzGKXBpexp_ke\'\n               \t\t});\n                }\n     \t\t};\n  </script>\n  <!-- END CAPTCHA -->\n  <meta content="width=device-width, initial-scale=1.0, maximum-scale=1.0, user-scalable=no" name="viewport"/>\n  <title>\n   Travel Advisories\n  </title>\n  <link href="/apps/tsg-rwd/components/content/tsg-rwd-top-sitewide-resource-menu/clientlib/css/tsg-rwd-top-sitewide-resource-menu.css" rel="stylesheet"/>\n  <link href="/apps/tsg-rwd/components/content/resources/favicon.ico" rel="shortcut icon" type="image/x-icon"/>\n  <meta content="/content/dam

In [30]:
div = soup.find('div', {'class': 'table-data simple_richtextarea'})

In [31]:
print (div)

<div class="table-data simple_richtextarea">


<table border="0" cellpadding="0" cellspacing="0">
<tbody><tr><td><b>Advisory</b></td>
<td><b>Level </b></td>
<td><b>Date updated</b></td>
</tr><tr><td valign="bottom"><p><a href="/content/travel/en/traveladvisories/traveladvisories/afghanistan-advisory.html">Afghanistan</a></p>
</td>
<td><p>4: Do not travel</p>
</td>
<td><p>2018-01-10</p>
</td>
</tr><tr><td valign="bottom"><p><a href="/content/travel/en/traveladvisories/traveladvisories/albania-travel-advisory.html">Albania</a></p>
</td>
<td valign="bottom"><p>1: Exercise normal precautions</p>
</td>
<td><p>2018-01-10</p>
</td>
</tr><tr><td valign="bottom"><p><a href="/content/travel/en/traveladvisories/traveladvisories/algeria-travel-advisory.html">Algeria</a></p>
</td>
<td><p>2: Exercise increased caution</p>
</td>
<td><p>2018-01-10</p>
</td>
</tr><tr><td valign="bottom"><p><a href="/content/travel/en/traveladvisories/traveladvisories/andorra-travel-advisory.html">Andorra</a></p>
</td>


In [32]:
country=[]
advice=[]
advice1=[]

for row in div.findAll("tr"):
    cells = row.findAll('td')
 
    if len(cells)==3: 
        country.append(cells[0].find(text=True))
        advice.append(cells[1].find(text=True))
        advice1.append(cells[2].find(text=True))

In [33]:
travel=pd.DataFrame(columns=['Number'])

travel['country']=country
travel['advice']=advice
travel['country'] = travel['country'].str.upper()
travel_advice = travel.drop(['Number'], axis=1)

In [34]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_ta = pd.merge(left=merged_gdp,right=travel_advice, how='left', left_on='country_of_citizenship', right_on='country')

In [35]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_ta2 = pd.merge(left=merged_gdp2,right=travel_advice, how='left', left_on='country_of_citizenship', right_on='country')

In [36]:
t_advice = merged_ta.groupby('advice').size().reset_index()
t_advice.sort_values(0, ascending=False)

advice      0
1   2: Exercise increased caution  21334
0  1: Exercise normal precautions   3253
2            3: Reconsider travel    932
4                4: Do not travel    123
3            3: Reconsider travel      9

In [37]:
merged_left = merged_ta

In [38]:
merged_left2= merged_ta2

In [39]:
merged_left.advice=merged_ta.advice.replace('3: Reconsider travel', '3:Reconsider travel')
merged_left2.advice=merged_ta2.advice.replace('3: Reconsider travel', '3:Reconsider travel')

In [40]:
merged_left.advice=merged_ta.advice.replace('3: Reconsider travel', '3:Reconsider travel')
merged_left2.advice=merged_ta2.advice.replace('3: Reconsider travel', '3:Reconsider travel')

We also binned decision date into years, in order to reduce the cardinality significantly and assess whether the case decision might have been influenced by the political force in power that year. 

In [41]:
# https://www.analyticsvidhya.com/blog/2015/10/beginner-guide-web-scraping-beautiful-soup-python/
url =('https://en.wikipedia.org/wiki/Political_party_strength_in_U.S._states')
party = urllib.request.urlopen(url)

In [42]:
soup = BeautifulSoup(party)

soup.prettify()

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("html5lib"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "html5lib")

  markup_type=markup_type))


'<!DOCTYPE html>\n<html class="client-nojs" dir="ltr" lang="en">\n <head>\n  <meta charset="utf-8"/>\n  <title>\n   Political party strength in U.S. states - Wikipedia\n  </title>\n  <script>\n   document.documentElement.className = document.documentElement.className.replace( /(^|\\s)client-nojs(\\s|$)/, "$1client-js$2" );\n  </script>\n  <script>\n   (window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Political_party_strength_in_U.S._states","wgTitle":"Political party strength in U.S. states","wgCurRevisionId":838907561,"wgRevisionId":838907561,"wgArticleId":898541,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Use mdy dates from December 2014","Articles containing potentially dated statements from October 2017","All articles containing potentially dated statements","Articles containing potentially dated statements f

In [43]:
tables=soup.find_all('table')

tables

[<table class="wikitable" style="margin: 1em auto 1em auto; text-align:center;">
 <caption>Partisan lean of U.S. states according to Gallup polling<sup class="reference" id="cite_ref-Gallup-2014-states_5-1"><a href="#cite_note-Gallup-2014-states-5">[5]</a></sup></caption>
 <tbody><tr>
 <th> </th>
 <th colspan="6">Number of U.S. States</th>
 </tr>
 <tr>
 <th width="16%">Year</th>
 <th width="14%">Solid Dem</th>
 <th width="14%">Lean Dem</th>
 <th width="14%">Competitive</th>
 <th width="14%">Lean GOP</th>
 <th width="14%">Solid GOP</th>
 <th width="14%">Net Dem</th>
 </tr>
 <tr>
 <td>2008</td>
 <td>29</td>
 <td>6</td>
 <td>10</td>
 <td>1</td>
 <td>4</td>
 <td>+30</td>
 </tr>
 <tr>
 <td>2009</td>
 <td>23</td>
 <td>10</td>
 <td>12</td>
 <td>1</td>
 <td>4</td>
 <td>+28</td>
 </tr>
 <tr>
 <td>2010</td>
 <td>13</td>
 <td>9</td>
 <td>18</td>
 <td>5</td>
 <td>5</td>
 <td>+12</td>
 </tr>
 <tr>
 <td>2011</td>
 <td>11</td>
 <td>7</td>
 <td>15</td>
 <td>7</td>
 <td>10</td>
 <td>+1</td>
 </tr>
 <tr

In [44]:
party_table=soup.find_all('table', class_='wikitable')[1]

print (party_table)

<table class="wikitable" width="100%">
<tbody><tr align="center">
<th width="11%">State</th>
<th width="12%">2016 Presidential<br/>
Election</th>
<th width="11%">Governor</th>
<th width="11%">State Senate</th>
<th width="11%">State House</th>
<th width="11%">Senior<br/>
U.S. Senator</th>
<th width="11%">Junior<br/>
U.S. Senator</th>
<th width="11%">U.S. House of Representatives</th>
<th width="11%">Partisan Split (as of 2014<sup class="plainlinks noexcerpt noprint asof-tag update" style="display:none;"><a class="external text" href="//en.wikipedia.org/w/index.php?title=Political_party_strength_in_U.S._states&amp;action=edit">[update]</a></sup>)</th>
</tr>
<tr align="center">
<td><a href="/wiki/Alabama" title="Alabama">Alabama</a></td>
<td style="background:#FFB6B6">Republican</td>
<td style="background:#FFB6B6">Republican</td>
<td style="background:#FFB6B6">Republican 26-7-1<sup>(a)</sup></td>
<td style="background:#FFB6B6">Republican 70-32</td>
<td style="background:#FFB6B6">Republica

In [45]:
state = []
party=[]
count=0
for row in party_table.findAll("tr"):
    cells = row.findAll('td')
    cells = str(cells[1:2])
    cells = cells.strip(']')
    cells = cells.strip('[')
    links = row.findAll('a')

    if count != 0:
        state_found = links[0].find(text=True)
        state.append(state_found.upper())
        
        m = re.search("(<td style=\"background:#)([A-Z\d]+)(\">)\W*([A-Z][a-z]+)(</td>)",cells)
        if m:
            party.append(m.group(4))
        
    else:
        count+=1

In [46]:
party_df=pd.DataFrame(columns=['Number'])

party_df['State']=state 
party_df['Party']=party

party_df = party_df.drop(['Number'], axis=1)

In [47]:
# #http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left = pd.merge(left=merged_left,right=party_df, how='left', left_on='employer_state', right_on='State')
merged_left =merged_left.drop('State', axis = 1)

In [48]:
# #http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left2 = pd.merge(left=merged_left2,right=party_df, how='left', left_on='employer_state', right_on='State')
merged_left2 =merged_left2.drop('State', axis = 1)

In [49]:
titles = merged_left['pw_soc_title'].values

In [50]:
titles2 = merged_left2['pw_soc_title'].values

In [51]:
industry = []
title = []

for word in titles:
    word = str(word)
    r = re.compile(r' Educat | Teacher | Instructional ', flags=re.I | re.X)
    if r.findall(word):
        #print(word)
        industry.append('Education')
        title.append(word)
    else:
        r = re.compile(r' Software | Computer | \bDatabase\b | Web | Data | Graphic', flags=re.I | re.X) #(?<!Except ).
        if r.findall(word):
                #print(word)
                industry.append('Technology')
                title.append(word)
        else:
            r = re.compile(r' Sale | Market | Advertising | Training | Relations | Purchasing ', flags=re.I | re.X)
            if r.findall(word):
                #print(word)
                industry.append('Sales and Marketing')
                title.append(word)
            else:
                r = re.compile(r' Engineer | Operations | Architect | Construction |  Industrial | Estimators | logistic | Distribution', flags=re.I | re.X)  
                if r.findall(word):
                    #print(word)
                    industry.append('Construction and Engineering')
                    title.append(word)
                else:
                    r = re.compile(r' Health | Medic | Thera | Obstetrician | Dietit | Anesthes | General | Dentist | Podiat | Surgeon | Psychiatrists | Pharma | Speech | Vet', flags=re.I | re.X)
                    if r.findall(word):
                        #print(word)
                        industry.append('Health and Medicine')
                        title.append(word)
                    else:
                        r = re.compile(r' Scien | Bio | Chem | Lab | Geo | Phys | Math', flags=re.I | re.X)
                        if r.findall(word):
                            #print(word)
                            industry.append('Science')
                            title.append(word)
                        else:
                            r = re.compile(r' Finan | Insurance | Account |  Clerk | Econ | Treasurers | Audit | Statis | Compliance | Chief | Analyst | Actuaries', flags=re.I | re.X)
                            if r.findall(word):
                                #print(word)
                                industry.append('Accounting and Finance')
                                title.append(word)
                            else:
                                r = re.compile(r' Law | Legal ', flags=re.I | re.X)
                                if r.findall(word):
                                    #print(word)
                                    industry.append('Law')
                                    title.append(word)
                                else:
                                    if word != 'nan':
                                        industry.append('Other')
                                        title.append(word)
                                        #print(word)
                                    else:
                                        
                                        industry.append('Blank')
                                        title.append(word)


In [52]:
sector_df=pd.DataFrame(columns=['Number'])

sector_df['Industry']=industry
sector_df['pw_soc_title']=title
#sector_df[]
sector_df = sector_df.drop(['Number'], axis=1)
sector_df

Industry  \
0               Health and Medicine   
1                        Technology   
2            Accounting and Finance   
3                        Technology   
4      Construction and Engineering   
5                         Education   
6            Accounting and Finance   
7                         Education   
8                        Technology   
9                        Technology   
10                       Technology   
11                       Technology   
12                       Technology   
13                        Education   
14                       Technology   
15                       Technology   
16                       Technology   
17                       Technology   
18              Sales and Marketing   
19           Accounting and Finance   
20                       Technology   
21                       Technology   
22                        Education   
23                       Technology   
24                       Technology   
25                       Technology   
26                       Technology   
27                       Technology   
28                        Education   
29                       Technology   
30                       Technology   
31                            Blank   
32                       Technology   
33                       Technology   
34                       Technology   
35                       Technology   
36              Sales and Marketing   
37              Sales and Marketing   
38                       Technology   
39                       Technology   
40                       Technology   
41                            Other   
42                       Technology   
43                       Technology   
44                       Technology   
45                       Technology   
46                       Technology   
47                            Other   
48              Health and Medicine   
49              Sales and Marketing   
50                       Technology   
51                        Education   
52              Sales and Marketing   
53                       Technology   
54                          Science   
55              Sales and Marketing   
56           Accounting and Finance   
57              Health and Medicine   
58                       Technology   
59                       Technology   
60                        Education   
61                       Technology   
62           Accounting and Finance   
63                       Technology   
64                       Technology   
65                       Technology   
66                       Technology   
67           Accounting and Finance   
68                       Technology   
69                       Technology   
70                       Technology   
71     Construction and Engineering   
72                        Education   
73                       Technology   
74                       Technology   
75                       Technology   
76                       Technology   
77              Health and Medicine   
78                            Blank   
79                       Technology   
80           Accounting and Finance   
81           Accounting and Finance   
82                       Technology   
83              Health and Medicine   
84                       Technology   
85                       Technology   
86                       Technology   
87     Construction and Engineering   
88                       Technology   
89                        Education   
90           Accounting and Finance   
91                       Technology   
92                       Technology   
93                       Technology   
94           Accounting and Finance   
95     Construction and Engineering   
96     Construction and Engineering   
97                       Technology   
98                       Technology   
99                       Technology   
100                      Technology   
101    Construction and Engineering   
102       

In [53]:
merged = pd.merge(merged_left[10:], sector_df[10:], left_index=True, right_index=True)

merged_left = merged.drop(['pw_soc_title_y'], axis=1)

In [54]:
industry = []
title = []

for word in titles2:
    word = str(word)
    r = re.compile(r' Educat | Teacher | Instructional ', flags=re.I | re.X)
    if r.findall(word):
        #print(word)
        industry.append('Education')
        title.append(word)
    else:
        r = re.compile(r' Software | Computer | \bDatabase\b | Web | Data | Graphic', flags=re.I | re.X) #(?<!Except ).
        if r.findall(word):
                #print(word)
                industry.append('Technology')
                title.append(word)
        else:
            r = re.compile(r' Sale | Market | Advertising | Training | Relations | Purchasing ', flags=re.I | re.X)
            if r.findall(word):
                #print(word)
                industry.append('Sales and Marketing')
                title.append(word)
            else:
                r = re.compile(r' Engineer | Operations | Architect | Construction |  Industrial | Estimators | logistic | Distribution', flags=re.I | re.X)  
                if r.findall(word):
                    #print(word)
                    industry.append('Construction and Engineering')
                    title.append(word)
                else:
                    r = re.compile(r' Health | Medic | Thera | Obstetrician | Dietit | Anesthes | General | Dentist | Podiat | Surgeon | Psychiatrists | Pharma | Speech | Vet', flags=re.I | re.X)
                    if r.findall(word):
                        #print(word)
                        industry.append('Health and Medicine')
                        title.append(word)
                    else:
                        r = re.compile(r' Scien | Bio | Chem | Lab | Geo | Phys | Math', flags=re.I | re.X)
                        if r.findall(word):
                            #print(word)
                            industry.append('Science')
                            title.append(word)
                        else:
                            r = re.compile(r' Finan | Insurance | Account |  Clerk | Econ | Treasurers | Audit | Statis | Compliance | Chief | Analyst | Actuaries', flags=re.I | re.X)
                            if r.findall(word):
                                #print(word)
                                industry.append('Accounting and Finance')
                                title.append(word)
                            else:
                                r = re.compile(r' Law | Legal ', flags=re.I | re.X)
                                if r.findall(word):
                                    #print(word)
                                    industry.append('Law')
                                    title.append(word)
                                else:
                                    if word != 'nan':
                                        industry.append('Other')
                                        title.append(word)
                                        #print(word)
                                    else:
                                        
                                        industry.append('Blank')
                                        title.append(word)


In [55]:
sector_df=pd.DataFrame(columns=['Number'])

sector_df['Industry']=industry
sector_df['pw_soc_title']=title
#sector_df[]
sector_df = sector_df.drop(['Number'], axis=1)
sector_df

Industry  \
0                         Technology   
1                Health and Medicine   
2                         Technology   
3             Accounting and Finance   
4                         Technology   
5                         Technology   
6                         Technology   
7                         Technology   
8                         Technology   
9                         Technology   
10      Construction and Engineering   
11                        Technology   
12                        Technology   
13                         Education   
14                        Technology   
15               Sales and Marketing   
16            Accounting and Finance   
17                         Education   
18      Construction and Engineering   
19                        Technology   
20                        Technology   
21                        Technology   
22                        Technology   
23               Sales and Marketing   
24                        Technology   
25                               Law   
26                        Technology   
27      Construction and Engineering   
28      Construction and Engineering   
29                         Education   
30                        Technology   
31      Construction and Engineering   
32               Sales and Marketing   
33                        Technology   
34                        Technology   
35                         Education   
36               Health and Medicine   
37                        Technology   
38                        Technology   
39                        Technology   
40                        Technology   
41                        Technology   
42      Construction and Engineering   
43                         Education   
44                        Technology   
45      Construction and Engineering   
46            Accounting and Finance   
47                        Technology   
48                         Education   
49            Accounting and Finance   
50                        Technology   
51                        Technology   
52                        Technology   
53                             Other   
54                        Technology   
55                        Technology   
56                        Technology   
57                        Technology   
58                        Technology   
59                             Other   
60                        Technology   
61                             Other   
62      Construction and Engineering   
63      Construction and Engineering   
64                        Technology   
65                        Technology   
66                        Technology   
67               Health and Medicine   
68                        Technology   
69                        Technology   
70                        Technology   
71                        Technology   
72                             Blank   
73               Sales and Marketing   
74               Health and Medicine   
75                        Technology   
76                        Technology   
77                        Technology   
78                        Technology   
79                        Technology   
80                        Technology   
81                        Technology   
82                        Technology   
83               Health and Medicine   
84               Sales and Marketing   
85                        Technology   
86                        Technology   
87                        Technology   
88            Accounting and Finance   
89                        Technology   
90               Health and Medicine   
91                        Technology   
92                        Technology   
93                        Technology   
94                        Technology   
95                        Technology   
96                        Technology   
97                        Technology   
98                        Technology   
99                         E

In [56]:
merged = pd.merge(merged_left2[10:], sector_df[10:], left_index=True, right_index=True)

merged_left2 = merged.drop(['pw_soc_title_y'], axis=1)

In [57]:
merged_left

case_status    country_of_citizenship decision_date  \
10         Denied                     INDIA    2015-02-20   
11         Denied                     INDIA    2015-05-15   
12         Denied                       NaN    2012-01-31   
13         Denied                 VENEZUELA    2014-11-14   
14         Denied                     INDIA    2013-11-14   
15      Certified                     INDIA    2015-09-16   
16         Denied                       NaN    2011-10-27   
17      Certified                BANGLADESH    2014-06-09   
18         Denied                       NaN    2011-10-21   
19         Denied                    CANADA    2016-05-09   
20      Certified                     NEPAL    2016-08-26   
21      Certified                     INDIA    2016-07-29   
22         Denied                    TAIWAN    2016-01-05   
23      Certified                       NaN    2011-12-23   
24         Denied                     INDIA    2013-08-13   
25      Certified                     INDIA    2016-04-21   
26         Denied               SOUTH KOREA    2014-11-07   
27      Certified                    TAIWAN    2016-08-05   
28         Denied               PHILIPPINES    2015-04-10   
29      Certified                     INDIA    2015-08-10   
30      Certified                     INDIA    2016-06-02   
31         Denied               SOUTH KOREA    2012-12-20   
32      Certified                   GERMANY    2015-08-26   
33      Certified                     INDIA    2016-09-30   
34      Certified                     INDIA    2016-07-15   
35         Denied                     INDIA    2015-07-10   
36         Denied                UZBEKISTAN    2014-05-12   
37      Certified                     JAPAN    2013-09-26   
38         Denied                     CHINA    2016-09-29   
39      Certified                     INDIA    2014-09-11   
40         Denied                     INDIA    2013-02-13   
41      Certified               SOUTH KOREA    2014-05-29   
42         Denied                    CANADA    2013-02-04   
43      Certified                     INDIA    2014-09-26   
44      Certified                     INDIA    2015-06-25   
45         Denied            UNITED KINGDOM    2014-06-16   
46         Denied                     INDIA    2014-06-18   
47         Denied                     INDIA    2016-01-19   
48      Certified               PHILIPPINES    2014-05-06   
49      Certified                     CHINA    2014-06-03   
50         Denied                     INDIA    2016-12-16   
51         Denied                     INDIA    2013-03-08   
52      Certified                    CANADA    2016-08-04   
53      Certified                     INDIA    2016-09-15   
54         Denied                       NaN    2012-01-03   
55      Certified                     INDIA    2015-05-04   
56      Certified                     CHINA    2016-09-27   
57      Certified                     INDIA    2013-08-29   
58         Denied                    SWEDEN    2016-08-18   
59      Certified                     INDIA    2016-12-21   
60      Certified                     CHINA    2016-12-01   
61         Denied                     INDIA    2016-02-05   
62      Certified                    BRAZIL    2016-12-27   
63      Certified                     INDIA    2016-08-18   
64      Certified                     INDIA    2013-09-20   
65      Certified                     INDIA    2016-05-05   
66         Denied                     CHINA    2015-03-04   
67         Denied                  COLOMBIA    2014-04-03   
68      Certified                     INDIA    2014-07-10   
69      Certified                     INDIA    2014-08-29   
70         Denied                    CANADA    2016-10-25   
71         Denied                    CANADA    2016-01-25   
72         Denied               PHILIPPINES    2014-03-11   
73         Denied                     CHINA    2016-09-13   
74         Denied                  COLOMB

In [58]:
merged_left2

case_status    country_of_citizenship decision_date  \
10       Certified                    TURKEY    2014-06-06   
11          Denied                     INDIA    2015-04-22   
12       Certified                     INDIA    2015-05-01   
13       Certified                       NaN    2011-12-30   
14       Certified                       NaN    2011-12-07   
15       Certified                     INDIA    2016-06-13   
16       Certified                     INDIA    2014-05-09   
17       Certified                     CHINA    2014-07-15   
18          Denied                     CHINA    2013-11-14   
19       Certified                     INDIA    2016-08-04   
20       Certified                     INDIA    2014-08-29   
21       Certified                     INDIA    2014-09-08   
22       Certified                     INDIA    2016-06-02   
23       Certified                     INDIA    2016-08-17   
24       Certified                     INDIA    2015-05-07   
25       Certified                       NaN    2012-03-01   
26          Denied               PHILIPPINES    2012-12-04   
27       Certified                    TURKEY    2016-06-17   
28       Certified                     KENYA    2014-04-09   
29          Denied                       NaN    2012-01-18   
30       Certified                     INDIA    2014-09-02   
31       Certified                     INDIA    2014-04-10   
32       Certified                     INDIA    2014-06-05   
33       Certified                    CANADA    2016-09-22   
34       Certified                     INDIA    2016-05-12   
35       Certified                   UKRAINE    2016-07-14   
36       Certified                   BELGIUM    2016-06-15   
37          Denied                     INDIA    2016-04-06   
38       Certified                     INDIA    2015-07-22   
39       Certified                     INDIA    2014-04-22   
40       Certified                     INDIA    2016-11-21   
41       Certified                     INDIA    2016-09-20   
42          Denied                       NaN    2012-03-20   
43          Denied                       NaN    2011-11-14   
44       Certified                     INDIA    2014-07-21   
45       Certified                       NaN    2012-02-17   
46       Certified                     INDIA    2014-06-06   
47       Certified                     INDIA    2014-04-23   
48       Certified                       NaN    2012-03-01   
49          Denied                     CHINA    2015-08-10   
50       Certified                   JAMAICA    2013-07-23   
51       Certified                     INDIA    2014-09-05   
52       Certified                     CHINA    2016-04-29   
53       Certified               SOUTH KOREA    2014-08-19   
54       Certified                     INDIA    2016-09-19   
55       Certified                     CHINA    2016-07-11   
56       Certified                     INDIA    2016-04-25   
57       Certified                     INDIA    2016-05-02   
58       Certified                     CHINA    2016-04-13   
59       Certified                    FRANCE    2016-10-24   
60       Certified                     INDIA    2015-08-14   
61       Certified                   UKRAINE    2015-09-22   
62       Certified                     CHINA    2016-12-19   
63       Certified                       NaN    2012-03-21   
64       Certified                     INDIA    2016-07-07   
65       Certified                     INDIA    2015-08-18   
66       Certified                     INDIA    2016-12-21   
67       Certified                     INDIA    2014-04-14   
68       Certified                     INDIA    2014-08-26   
69       Certified                     INDIA    2016-06-15   
70       Certified                     INDIA    2016-10-31   
71       Certified                     INDIA    2015-09-02   
72          Denied                     INDIA    2013-03-05   
73          Denied                     

In [59]:
merged_left.head()

case_status country_of_citizenship decision_date  \
10      Denied                  INDIA    2015-02-20   
11      Denied                  INDIA    2015-05-15   
12      Denied                    NaN    2012-01-31   
13      Denied              VENEZUELA    2014-11-14   
14      Denied                  INDIA    2013-11-14   

                  employer_address_1 employer_city  \
10               103 CARNEIGIE DRIVE     PRINCETON   
11     6100 TENNYSON PKWY, SUITE 200         PLANO   
12                  12777 JONES ROAD       HOUSTON   
13                    3807 ROSS AVE.        DALLAS   
14  63 RAMAPO VALLEY ROAD, SUITE 214        MAHWAH   

                         employer_name employer_postal_code employer_state  \
10            KRYPTO IT SOLUTIONS, INC                08540     NEW JERSEY   
11        INFOSYS TECHNOLOGIES LIMITED                75024          TEXAS   
12        ADVENT GLOBAL SOLUTIONS,INC.              77070.0          TEXAS   
13  DALLAS INDEPENDENT SCHOOL DISTRICT                75204          TEXAS   
14                     FABERGENT, INC.                 7430     NEW JERSEY   

                    pw_job_title_9089 pw_level_9089 pw_soc_code  \
10  Software Developers, Applications      Level II     15-1132   
11          Computer Systems Analysts      Level II  15-1051.00   
12             Sr. Programmer/Analyst      Level II  15-1021.00   
13       ELEMENTARY BILINGUAL TEACHER       Level I     25-2021   
14          Computer Systems Analysts     Level III     15-1121   

                                       pw_soc_title_x pw_source_name_9089  \
10                  Software Developers, Applications                 OES   
11                          Computer Systems Analysts                 OES   
12                               Computer Programmers                 OES   
13  Elementary School Teachers, Except Special Edu...                 OES   
14                          Computer Systems Analysts                 OES   

   pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
10                Year                        Year                 0  139   
11                Year                        Year                 0  139   
12                Year                        Year                 0  NaN   
13                Year                        Year                 0   81   
14                Year                         NaN                 0  139   

       GDP     GDPGroups    country                         advice  \
10  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   
11  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   
12     NaN           NaN        NaN                            NaN   
13  6684.0  Mid Rank GDP  VENEZUELA            3:Reconsider travel   
14  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   

         Party    Industry  
10  Democratic  Technology  
11  Republican  Technology  
12  Republican  Technology  
13  Republican   Education  
14  Democratic  Technology

In [60]:
merged_left2.head()

case_status country_of_citizenship decision_date  \
10   Certified                 TURKEY    2014-06-06   
11      Denied                  INDIA    2015-04-22   
12   Certified                  INDIA    2015-05-01   
13   Certified                    NaN    2011-12-30   
14   Certified                    NaN    2011-12-07   

            employer_address_1 employer_city             employer_name  \
10  3225 OAKMEAD VILLAGE DRIVE   SANTA CLARA   APPLIED MATERIALS, INC.   
11        3039 CORNWALLIS ROAD           RTP           IBM CORPORATION   
12  2200 MISSION COLLEGE BLVD.   SANTA CLARA         INTEL CORPORATION   
13               PO BOX 874311         TEMPE  ARIZONA STATE UNIVERSITY   
14        5775 MOREHOUSE DRIVE     SAN DIEGO            QUALCOMM, INC.   

   employer_postal_code  employer_state pw_level_9089 pw_soc_code  \
10                95054      CALIFORNIA           NaN     17-2131   
11                27709  NORTH CAROLINA      Level II     15-1132   
12                95052      CALIFORNIA           NaN     17-2072   
13              85287.0         ARIZONA       Level I  25-1021.00   
14              92121.0      CALIFORNIA      Level II  15-1032.00   

                                   pw_soc_title_x pw_source_name_9089  \
10                            Materials Engineers               Other   
11              Software Developers, Applications                 OES   
12         Electronics Engineers, Except Computer               Other   
13       Computer Science Teachers, Postsecondary                 OES   
14  Computer Software Engineers, Systems Software                 OES   

   pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
10                Year                         NaN                 1   63   
11                Year                        Year                 0  139   
12                Year                        Year                 1  139   
13                Year                        Year                 1  NaN   
14                Year                        Year                 1  NaN   

        GDP      GDPGroups country                         advice       Party  \
10  10512.0  High Rank GDP  TURKEY            3:Reconsider travel  Democratic   
11   1983.0   Low Rank GDP   INDIA  2: Exercise increased caution  Republican   
12   1983.0   Low Rank GDP   INDIA  2: Exercise increased caution  Democratic   
13      NaN            NaN     NaN                            NaN  Republican   
14      NaN            NaN     NaN                            NaN  Democratic   

                        Industry  
10  Construction and Engineering  
11                    Technology  
12                    Technology  
13                     Education  
14                    Technology

In [61]:
merged_left.decision_date.value_counts()

2016-06-20    119
2015-08-28    117
2016-08-29    113
2015-05-15    111
2015-09-18    111
2016-11-02     99
2015-09-01     93
2016-10-26     82
2015-07-30     81
2014-05-06     80
2015-04-13     78
2015-09-21     77
2016-05-26     76
2012-01-31     75
2016-07-28     74
2016-12-21     73
2015-09-04     73
2014-06-04     72
2013-09-26     72
2016-07-08     72
2013-09-05     71
2015-05-20     70
2013-01-25     69
2015-04-14     68
2016-09-12     68
2012-03-29     67
2014-10-15     66
2016-07-11     65
2012-03-28     65
2014-05-07     64
2016-06-15     64
2016-05-19     64
2016-04-19     63
2015-05-21     63
2015-07-31     63
2016-05-11     63
2014-07-01     62
2016-04-25     62
2012-03-27     61
2016-04-27     61
2016-12-09     61
2016-08-05     60
2016-11-16     60
2016-06-13     60
2014-02-04     59
2015-09-25     59
2015-04-21     59
2016-08-01     59
2015-09-11     59
2013-09-27     58
2015-07-13     58
2012-01-30     58
2016-04-18     57
2016-07-27     57
2015-01-09     57
2016-09-02

In [62]:
# Changing to datetime type
merged_left['decision_date']=pd.to_datetime(merged_left['decision_date'], errors = 'coerce')

In [63]:
# Changing to datetime type
merged_left2['decision_date']=pd.to_datetime(merged_left2['decision_date'], errors = 'coerce')

In [64]:
merged_left.decision_date

10      2015-02-20
11      2015-05-15
12      2012-01-31
13      2014-11-14
14      2013-11-14
15      2015-09-16
16      2011-10-27
17      2014-06-09
18      2011-10-21
19      2016-05-09
20      2016-08-26
21      2016-07-29
22      2016-01-05
23      2011-12-23
24      2013-08-13
25      2016-04-21
26      2014-11-07
27      2016-08-05
28      2015-04-10
29      2015-08-10
30      2016-06-02
31      2012-12-20
32      2015-08-26
33      2016-09-30
34      2016-07-15
35      2015-07-10
36      2014-05-12
37      2013-09-26
38      2016-09-29
39      2014-09-11
40      2013-02-13
41      2014-05-29
42      2013-02-04
43      2014-09-26
44      2015-06-25
45      2014-06-16
46      2014-06-18
47      2016-01-19
48      2014-05-06
49      2014-06-03
50      2016-12-16
51      2013-03-08
52      2016-08-04
53      2016-09-15
54      2012-01-03
55      2015-05-04
56      2016-09-27
57      2013-08-29
58      2016-08-18
59      2016-12-21
60      2016-12-01
61      2016-02-05
62      2016

In [65]:
merged_left['decision_Year'] = merged_left['decision_date'].dt.year
merged_left['decision_Month'] = merged_left['decision_date'].dt.month
merged_left['decision_date'] = merged_left['decision_date'].dt.year

In [66]:
merged_left2['decision_Year'] = merged_left2['decision_date'].dt.year
merged_left2['decision_Month'] = merged_left2['decision_date'].dt.month
merged_left2['decision_date'] = merged_left2['decision_date'].dt.year

In [67]:
merged_left.head()

case_status country_of_citizenship  decision_date  \
10      Denied                  INDIA           2015   
11      Denied                  INDIA           2015   
12      Denied                    NaN           2012   
13      Denied              VENEZUELA           2014   
14      Denied                  INDIA           2013   

                  employer_address_1 employer_city  \
10               103 CARNEIGIE DRIVE     PRINCETON   
11     6100 TENNYSON PKWY, SUITE 200         PLANO   
12                  12777 JONES ROAD       HOUSTON   
13                    3807 ROSS AVE.        DALLAS   
14  63 RAMAPO VALLEY ROAD, SUITE 214        MAHWAH   

                         employer_name employer_postal_code employer_state  \
10            KRYPTO IT SOLUTIONS, INC                08540     NEW JERSEY   
11        INFOSYS TECHNOLOGIES LIMITED                75024          TEXAS   
12        ADVENT GLOBAL SOLUTIONS,INC.              77070.0          TEXAS   
13  DALLAS INDEPENDENT SCHOOL DISTRICT                75204          TEXAS   
14                     FABERGENT, INC.                 7430     NEW JERSEY   

                    pw_job_title_9089 pw_level_9089 pw_soc_code  \
10  Software Developers, Applications      Level II     15-1132   
11          Computer Systems Analysts      Level II  15-1051.00   
12             Sr. Programmer/Analyst      Level II  15-1021.00   
13       ELEMENTARY BILINGUAL TEACHER       Level I     25-2021   
14          Computer Systems Analysts     Level III     15-1121   

                                       pw_soc_title_x pw_source_name_9089  \
10                  Software Developers, Applications                 OES   
11                          Computer Systems Analysts                 OES   
12                               Computer Programmers                 OES   
13  Elementary School Teachers, Except Special Edu...                 OES   
14                          Computer Systems Analysts                 OES   

   pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
10                Year                        Year                 0  139   
11                Year                        Year                 0  139   
12                Year                        Year                 0  NaN   
13                Year                        Year                 0   81   
14                Year                         NaN                 0  139   

       GDP     GDPGroups    country                         advice  \
10  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   
11  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   
12     NaN           NaN        NaN                            NaN   
13  6684.0  Mid Rank GDP  VENEZUELA            3:Reconsider travel   
14  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution   

         Party    Industry  decision_Year  decision_Month  
10  Democratic  Technology           2015               2  
11  Republican  Technology           2015               5  
12  Republican  Technology           2012               1  
13  Republican   Education           2014              11  
14  Democratic  Technology           2013              11

In [68]:
# https://www.analyticsvidhya.com/blog/2015/10/beginner-guide-web-scraping-beautiful-soup-python/
url =('http://www.nationsonline.org/oneworld/US-states-by-area.htm')
region = urllib.request.urlopen(url)

In [69]:
soup = BeautifulSoup(region)
soup.prettify()

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("html5lib"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "html5lib")

  markup_type=markup_type))


'<!DOCTYPE html>\n<html>\n <head>\n  <meta charset="utf-8"/>\n  <meta content="width=device-width, initial-scale=1" name="viewport"/>\n  <title>\n   List of US States by Area - Nations Online Project\n  </title>\n  <meta content="US states by area, largest US states, smallest US states by area, area of a state, list of US states by area, area, surface area, total area" name="keywords"/>\n  <meta content="From the largest to the smallest state of the United States. A list of all US States by total area in square kilometers and square miles." name="description"/>\n  <meta content="klaus kästle - nationsonline.org" name="author"/>\n  <meta content="index,follow" name="robots"/>\n  <meta content="99 days" name="revisit-after"/>\n  <meta content="http://www.nationsonline.org/oneworld/US-states-by-area.htm" property="og:url"/>\n  <meta content="website" property="og:type"/>\n  <meta content="List of US States by Area - Nations Online Project" property="og:title"/>\n  <meta content="From the 

In [70]:
tables=soup.find_all('table', 'statelist')

In [71]:
region_table=soup.find('table', id='statelist')

In [72]:
state=[]
census_region=[]

for row in region_table.findAll("tr"):
    cells = row.findAll('td')
    links = row.findAll('a')
    print("cells are ", cells)
 
    if len(cells)==8: 
        census_region.append(cells[6].find(text=True))
        state.append(links[1].find(text=True))

cells are  []
cells are  [<td>30</td>, <td><a href="javascript:;" onclick="MM_openBrWindow('../flags_big/Alabama_Flag.html','Alabama','width=650,height=520')"><img alt="Alabama State Flag" height="14" src="../U.S.Flags/alabama_state_flag.gif" width="20"/></a></td>, <td><a href="map/USA/alabama_map.htm">Alabama</a></td>, <td style="text-align:right">135,767</td>, <td style="text-align:right">52,420 </td>, <td> </td>, <td>East South Central</td>, <td>Largest state in East South Central region</td>]
cells are  [<td>1</td>, <td><a href="javascript:;" onclick="MM_openBrWindow('../flags_big/Alaska_Flag.html','Alaska','width=650,height=520')"><img alt="Alaska State Flag" height="14" src="../U.S.Flags/alaska_state_flag.gif" width="20"/></a></td>, <td><a href="map/USA/alaska_map.htm">Alaska</a></td>, <td style="text-align:right">1,723,336</td>, <td style="text-align:right">665,384 </td>, <td> </td>, <td>Pacific</td>, <td>Largest state in the US, not bordered by any other US state</td>]
cells ar

In [73]:
region=pd.DataFrame(columns=['Number'])

region['State']=state
region['CensusRegion']=census_region
region['employer_state'] = region['State'].str.upper()

regions = region.drop(['Number', 'State'], axis=1)

In [74]:
regions.head(5)

CensusRegion employer_state
0  East South Central        ALABAMA
1             Pacific         ALASKA
2            Mountain        ARIZONA
3  West South Central       ARKANSAS
4             Pacific     CALIFORNIA

In [75]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left = pd.merge(left=merged_left,right=regions, how='left', left_on='employer_state', right_on='employer_state')

In [76]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left2 = pd.merge(left=merged_left2,right=regions, how='left', left_on='employer_state', right_on='employer_state')

In [77]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left.head(5)

case_status country_of_citizenship  decision_date  \
0      Denied                  INDIA           2015   
1      Denied                  INDIA           2015   
2      Denied                    NaN           2012   
3      Denied              VENEZUELA           2014   
4      Denied                  INDIA           2013   

                 employer_address_1 employer_city  \
0               103 CARNEIGIE DRIVE     PRINCETON   
1     6100 TENNYSON PKWY, SUITE 200         PLANO   
2                  12777 JONES ROAD       HOUSTON   
3                    3807 ROSS AVE.        DALLAS   
4  63 RAMAPO VALLEY ROAD, SUITE 214        MAHWAH   

                        employer_name employer_postal_code employer_state  \
0            KRYPTO IT SOLUTIONS, INC                08540     NEW JERSEY   
1        INFOSYS TECHNOLOGIES LIMITED                75024          TEXAS   
2        ADVENT GLOBAL SOLUTIONS,INC.              77070.0          TEXAS   
3  DALLAS INDEPENDENT SCHOOL DISTRICT                75204          TEXAS   
4                     FABERGENT, INC.                 7430     NEW JERSEY   

                   pw_job_title_9089 pw_level_9089 pw_soc_code  \
0  Software Developers, Applications      Level II     15-1132   
1          Computer Systems Analysts      Level II  15-1051.00   
2             Sr. Programmer/Analyst      Level II  15-1021.00   
3       ELEMENTARY BILINGUAL TEACHER       Level I     25-2021   
4          Computer Systems Analysts     Level III     15-1121   

                                      pw_soc_title_x pw_source_name_9089  \
0                  Software Developers, Applications                 OES   
1                          Computer Systems Analysts                 OES   
2                               Computer Programmers                 OES   
3  Elementary School Teachers, Except Special Edu...                 OES   
4                          Computer Systems Analysts                 OES   

  pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
0                Year                        Year                 0  139   
1                Year                        Year                 0  139   
2                Year                        Year                 0  NaN   
3                Year                        Year                 0   81   
4                Year                         NaN                 0  139   

      GDP     GDPGroups    country                         advice       Party  \
0  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution  Democratic   
1  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution  Republican   
2     NaN           NaN        NaN                            NaN  Republican   
3  6684.0  Mid Rank GDP  VENEZUELA            3:Reconsider travel  Republican   
4  1983.0  Low Rank GDP      INDIA  2: Exercise increased caution  Democratic   

     Industry  decision_Year  decision_Month        CensusRegion  
0  Technology           2015               2     Middle Atlantic  
1  Technology           2015               5  West South Central  
2  Technology           2012               1  West South Central  
3   Education           2014              11  West South Central  
4  Technology           2013              11     Middle Atlantic

In [78]:
#http://chris.friedline.net/2015-12-15-rutgers/lessons/python2/04-merging-data.html
merged_left2.head(5)

case_status country_of_citizenship  decision_date  \
0   Certified                 TURKEY           2014   
1      Denied                  INDIA           2015   
2   Certified                  INDIA           2015   
3   Certified                    NaN           2011   
4   Certified                    NaN           2011   

           employer_address_1 employer_city             employer_name  \
0  3225 OAKMEAD VILLAGE DRIVE   SANTA CLARA   APPLIED MATERIALS, INC.   
1        3039 CORNWALLIS ROAD           RTP           IBM CORPORATION   
2  2200 MISSION COLLEGE BLVD.   SANTA CLARA         INTEL CORPORATION   
3               PO BOX 874311         TEMPE  ARIZONA STATE UNIVERSITY   
4        5775 MOREHOUSE DRIVE     SAN DIEGO            QUALCOMM, INC.   

  employer_postal_code  employer_state pw_level_9089 pw_soc_code  \
0                95054      CALIFORNIA           NaN     17-2131   
1                27709  NORTH CAROLINA      Level II     15-1132   
2                95052      CALIFORNIA           NaN     17-2072   
3              85287.0         ARIZONA       Level I  25-1021.00   
4              92121.0      CALIFORNIA      Level II  15-1032.00   

                                  pw_soc_title_x pw_source_name_9089  \
0                            Materials Engineers               Other   
1              Software Developers, Applications                 OES   
2         Electronics Engineers, Except Computer               Other   
3       Computer Science Teachers, Postsecondary                 OES   
4  Computer Software Engineers, Systems Software                 OES   

  pw_unit_of_pay_9089 wage_offer_unit_of_pay_9089  case_status_code Rank  \
0                Year                         NaN                 1   63   
1                Year                        Year                 0  139   
2                Year                        Year                 1  139   
3                Year                        Year                 1  NaN   
4                Year                        Year                 1  NaN   

       GDP      GDPGroups country                         advice       Party  \
0  10512.0  High Rank GDP  TURKEY            3:Reconsider travel  Democratic   
1   1983.0   Low Rank GDP   INDIA  2: Exercise increased caution  Republican   
2   1983.0   Low Rank GDP   INDIA  2: Exercise increased caution  Democratic   
3      NaN            NaN     NaN                            NaN  Republican   
4      NaN            NaN     NaN                            NaN  Democratic   

                       Industry  decision_Year  decision_Month    CensusRegion  
0  Construction and Engineering           2014               6         Pacific  
1                    Technology           2015               4  South Atlantic  
2                    Technology           2015               5         Pacific  
3                     Education           2011              12        Mountain  
4                    Technology           2011              12         Pacific

In [79]:
#merged_left.decision_date.value_counts()

In [80]:
# Dropping more columns as we won't be investigating further
# Some of these columns duplicate information in other columns, or are not of interest to us
merged_final = merged_left.drop(['employer_address_1', 'employer_city', 'employer_postal_code', 'pw_job_title_9089', 'pw_soc_code', 'Rank', 'wage_offer_unit_of_pay_9089'], axis=1)

In [81]:
# Dropping more columns as we won't be investigating further
# Some of these columns duplicate information in other columns, or are not of interest to us
merged_final_unbal = merged_left2.drop(['employer_address_1', 'employer_city', 'employer_postal_code', 'pw_soc_code', 'Rank', 'wage_offer_unit_of_pay_9089'], axis=1)

In [82]:
merged_final.head()

case_status country_of_citizenship  decision_date  \
0      Denied                  INDIA           2015   
1      Denied                  INDIA           2015   
2      Denied                    NaN           2012   
3      Denied              VENEZUELA           2014   
4      Denied                  INDIA           2013   

                        employer_name employer_state pw_level_9089  \
0            KRYPTO IT SOLUTIONS, INC     NEW JERSEY      Level II   
1        INFOSYS TECHNOLOGIES LIMITED          TEXAS      Level II   
2        ADVENT GLOBAL SOLUTIONS,INC.          TEXAS      Level II   
3  DALLAS INDEPENDENT SCHOOL DISTRICT          TEXAS       Level I   
4                     FABERGENT, INC.     NEW JERSEY     Level III   

                                      pw_soc_title_x pw_source_name_9089  \
0                  Software Developers, Applications                 OES   
1                          Computer Systems Analysts                 OES   
2                               Computer Programmers                 OES   
3  Elementary School Teachers, Except Special Edu...                 OES   
4                          Computer Systems Analysts                 OES   

  pw_unit_of_pay_9089  case_status_code     GDP     GDPGroups    country  \
0                Year                 0  1983.0  Low Rank GDP      INDIA   
1                Year                 0  1983.0  Low Rank GDP      INDIA   
2                Year                 0     NaN           NaN        NaN   
3                Year                 0  6684.0  Mid Rank GDP  VENEZUELA   
4                Year                 0  1983.0  Low Rank GDP      INDIA   

                          advice       Party    Industry  decision_Year  \
0  2: Exercise increased caution  Democratic  Technology           2015   
1  2: Exercise increased caution  Republican  Technology           2015   
2                            NaN  Republican  Technology           2012   
3            3:Reconsider travel  Republican   Education           2014   
4  2: Exercise increased caution  Democratic  Technology           2013   

   decision_Month        CensusRegion  
0               2     Middle Atlantic  
1               5  West South Central  
2               1  West South Central  
3              11  West South Central  
4              11     Middle Atlantic

In [83]:
merged_final_unbal.head()

case_status country_of_citizenship  decision_date             employer_name  \
0   Certified                 TURKEY           2014   APPLIED MATERIALS, INC.   
1      Denied                  INDIA           2015           IBM CORPORATION   
2   Certified                  INDIA           2015         INTEL CORPORATION   
3   Certified                    NaN           2011  ARIZONA STATE UNIVERSITY   
4   Certified                    NaN           2011            QUALCOMM, INC.   

   employer_state pw_level_9089  \
0      CALIFORNIA           NaN   
1  NORTH CAROLINA      Level II   
2      CALIFORNIA           NaN   
3         ARIZONA       Level I   
4      CALIFORNIA      Level II   

                                  pw_soc_title_x pw_source_name_9089  \
0                            Materials Engineers               Other   
1              Software Developers, Applications                 OES   
2         Electronics Engineers, Except Computer               Other   
3       Computer Science Teachers, Postsecondary                 OES   
4  Computer Software Engineers, Systems Software                 OES   

  pw_unit_of_pay_9089  case_status_code      GDP      GDPGroups country  \
0                Year                 1  10512.0  High Rank GDP  TURKEY   
1                Year                 0   1983.0   Low Rank GDP   INDIA   
2                Year                 1   1983.0   Low Rank GDP   INDIA   
3                Year                 1      NaN            NaN     NaN   
4                Year                 1      NaN            NaN     NaN   

                          advice       Party                      Industry  \
0            3:Reconsider travel  Democratic  Construction and Engineering   
1  2: Exercise increased caution  Republican                    Technology   
2  2: Exercise increased caution  Democratic                    Technology   
3                            NaN  Republican                     Education   
4                            NaN  Democratic                    Technology   

   decision_Year  decision_Month    CensusRegion  
0           2014               6         Pacific  
1           2015               4  South Atlantic  
2           2015               5         Pacific  
3           2011              12        Mountain  
4           2011              12         Pacific

We will now split my dataset into two - 70% into a training set and 30% into a test set. We will then examine the features and their interaction with the target feature more closely.

In [84]:
merged_final.shape

(28616, 19)

In [85]:
merged_final_unbal.shape

(153615, 19)

In [86]:
#Splitting the shuffled dataset into training and test set
df_train = merged_final[:20038]
df_train.head (10)
df_test = merged_final[20038:]
df_test.head(10)

case_status country_of_citizenship  decision_date  \
20038   Certified                  INDIA           2015   
20039   Certified                  CHINA           2016   
20040      Denied                  EGYPT           2016   
20041      Denied                  INDIA           2015   
20042      Denied                 MEXICO           2013   
20043   Certified                  INDIA           2016   
20044   Certified                  INDIA           2016   
20045   Certified                  INDIA           2016   
20046      Denied                 TURKEY           2013   
20047   Certified                  INDIA           2014   

                                         employer_name employer_state  \
20038                                   RADIUMSOFT INC        GEORGIA   
20039              MANAGEMENT SCIENCE ASSOCIATES, INC.   PENNSYLVANIA   
20040                                INTEL CORPORATION     CALIFORNIA   
20041                                       TRANSUNION       ILLINOIS   
20042           FORT WORTH INDEPENDENT SCHOOL DISTRICT          TEXAS   
20043  MASTECH, INC., A MASTECH HOLDINGS, INC. COMPANY   PENNSYLVANIA   
20044      THE PRUDENTIAL INSURANCE COMPANY OF AMERICA     NEW JERSEY   
20045                        emaestro Technologies Inc        GEORGIA   
20046                                     OZELMAS CORP       VIRGINIA   
20047                      LA CLINICA DE FAMILIA, INC.     NEW MEXICO   

      pw_level_9089                             pw_soc_title_x  \
20038      Level IV  Computer and Information Systems Managers   
20039      Level II          Software Developers, Applications   
20040      Level II      Software Developers, Systems Software   
20041      Level II          Software Developers, Applications   
20042           NaN                                        NaN   
20043      Level IV          Software Developers, Applications   
20044      Level IV          Software Developers, Applications   
20045     Level III                  Computer Systems Analysts   
20046      Level IV                  Computer Systems Analysts   
20047      Level IV                          Dentists, General   

      pw_source_name_9089 pw_unit_of_pay_9089  case_status_code      GDP  \
20038                 OES                Year                 1   1983.0   
20039                 OES                Year                 1   8643.0   
20040                 OES                Year                 0   2501.0   
20041                 OES                 NaN                 0   1983.0   
20042                 NaN                Year                 0   9304.0   
20043                 OES                Year                 1   1983.0   
20044                 OES                Year                 1   1983.0   
20045                 OES                Year                 1   1983.0   
20046                 OES                Year                 0  10512.0   
20047                 OES                Hour                 1   1983.0   

           GDPGroups country                         advice       Party  \
20038   Low Rank GDP   INDIA  2: Exercise increased caution  Republican   
20039   Mid Rank GDP   CHINA  2: Exercise increased caution  Republican   
20040   Mid Rank GDP   EGYPT  2: Exercise increased caution  Democratic   
20041   Low Rank GDP   INDIA  2: Exercise increased caution  Democratic   
20042  High Rank GDP  MEXICO  2: Exercise increased caution  Republican   
20043   Low Rank GDP   INDIA  2: Exercise increased caution  Republican   
20044   Low Rank GDP   INDIA  2: Exercise increased caution  Democratic   
20045   Low Rank GDP   INDIA  2: Exercise increased caution  Republican   
20046  High Rank GDP  TURKEY            3:Reconsider travel  Democratic   
20047   Low Rank GDP   INDIA  2: Exercise increased caution  Democratic   

                  Industry  decision_Year  decision_Month        CensusRegion  
20038           Technology           2015               9      South Atlantic  
20

In [87]:
# Creating a copy of the training and test datasets in order to manipulate them
df_test.loc
df_test.dtypes
test = df_test.copy()
df_train.loc
df_train.dtypes
train = df_train.copy()

## **Predictive Modeling:** Logistic Regression.  
 
On the training set we will train a logistic regression model to predict the target feature case_status_code, using only the descriptive features that appeared to show meaningful relationships with case_status_code in the graphs between features and the target feature.

The features we have chosed to use in this model are:
- decision_year
- decision_Month
- CensusRegion
- pw_unit_of_pay_9089
- pw_source_name_9089
- pw_level_9089

Below we will make dummy variables for the categorical features of interest, in preparation for training these features with the predictive model.

In [88]:
GDP_dummies = pd.get_dummies(train.GDPGroups, prefix='GDP')

In [89]:
payUnit_dummies = pd.get_dummies(train.pw_unit_of_pay_9089, prefix='Pay')

In [90]:
sourceName_dummies = pd.get_dummies(train.pw_source_name_9089, prefix='Source')
sourceName_dummies = sourceName_dummies.rename(columns=lambda x: x.replace(' ', '_'))


In [91]:
level_dummies = pd.get_dummies(train.pw_level_9089, prefix='L')
level_dummies = level_dummies.rename(columns=lambda x: x.replace(' ', '_'))


In [92]:
region_dummy = pd.get_dummies(train.CensusRegion, prefix='CR')
region_dummy = region_dummy.rename(columns=lambda x: x.replace(' ', '_'))


In [93]:
industry_dummy = pd.get_dummies(train.Industry, prefix='l')
industry_dummy = industry_dummy.rename(columns=lambda x: x.replace(' ', '_'))

Now that all necessary dummy variables are created below we will concatanate the dummy variables with the train dataframe into a new dataframe called df_new.

In [94]:
df_new = pd.concat([train, industry_dummy, region_dummy, GDP_dummies, payUnit_dummies, sourceName_dummies, level_dummies], axis = 1)

Now that the categorical features of interest are in dummy variables we will train a logistic regression model with these features below.

In [95]:
logreg = sm.logit(formula="case_status_code ~ decision_date + l_Technology + l_Accounting_and_Finance + l_Blank + l_Construction_and_Engineering + l_Education + l_Health_and_Medicine + l_Law + l_Other + l_Sales_and_Marketing + l_Science + decision_Month + CR_Middle_Atlantic + CR_East_North_Central + CR_Pacific + CR_New_England + CR_South_Atlantic + CR_East_South_Central + CR_West_North_Central + CR_Mountain + CR_West_South_Central + Pay_Year + Pay_Hour + L_Level_I + L_Level_II + L_Level_III + L_Level_IV + Source_CBA + Source_Employer_Conducted + Source_OES + Source_Other", data=df_new).fit()

print(logreg.params)

         Current function value: 0.614817
         Iterations: 35
Intercept                        -665.913823
decision_date                       0.354058
l_Technology                      -64.899415
l_Accounting_and_Finance          -65.004956
l_Blank                           -79.466816
l_Construction_and_Engineering    -64.982924
l_Education                       -65.552207
l_Health_and_Medicine             -64.863330
l_Law                             -65.203530
l_Other                           -65.606885
l_Sales_and_Marketing             -65.378228
l_Science                         -64.955566
decision_Month                      0.042811
CR_Middle_Atlantic                  0.496035
CR_East_North_Central               0.376488
CR_Pacific                          0.662528
CR_New_England                      0.828423
CR_South_Atlantic                   0.260353
CR_East_South_Central               0.574380
CR_West_North_Central               0.838435
CR_Mountain                       

/Users/Eimg/anaconda3/envs/comp47350/lib/python3.6/site-packages/statsmodels/base/model.py:496: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)


We will evaluate the importance of the trained features with this model by examining the coefficients in the models summary table.

In [96]:
print(logreg.summary())

                           Logit Regression Results                           
Dep. Variable:       case_status_code   No. Observations:                20038
Model:                          Logit   Df Residuals:                    20007
Method:                           MLE   Df Model:                           30
Date:                Mon, 30 Apr 2018   Pseudo R-squ.:                  0.1130
Time:                        21:13:19   Log-Likelihood:                -12320.
converged:                      False   LL-Null:                       -13889.
                                        LLR p-value:                     0.000
                                     coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------------------------
Intercept                       -665.9138   9.18e+05     -0.001      0.999    -1.8e+06     1.8e+06
decision_date                      0.3541      0.011     32.072      0.

In [97]:
logreg.predict(df_new).head(50)

0     5.279376e-01
1     4.879814e-01
2     2.172948e-01
3     3.073076e-01
4     4.816392e-01
5     6.469068e-01
6     2.473517e-01
7     4.822708e-01
8     2.767335e-01
9     6.379802e-01
10    6.732214e-01
11    6.808697e-01
12    4.059846e-01
13    2.378257e-01
14    4.793579e-01
15    5.783164e-01
16    5.767882e-01
17    7.087426e-01
18    2.756771e-01
19    5.200766e-01
20    5.863230e-01
21    3.191617e-14
22    6.621074e-01
23    8.039967e-01
24    6.998269e-01
25    7.254749e-01
26    4.353190e-01
27    3.865324e-01
28    7.175003e-01
29    4.766608e-01
30    3.552024e-01
31    3.023996e-01
32    3.732131e-01
33    4.425308e-01
34    6.105453e-01
35    6.422002e-01
36    4.352702e-01
37    2.143121e-01
38    5.001681e-01
39    4.458703e-01
40    7.980259e-01
41    2.934889e-01
42    6.336585e-01
43    7.230273e-01
44    2.142290e-01
45    5.187311e-01
46    6.319321e-01
47    4.308929e-01
48    7.362868e-01
49    7.698577e-01
dtype: float64

In [98]:
logregpredictions = logreg.predict(df_new).round()


In [99]:
y = df_new.case_status_code

In [100]:
print("Accuracy: ", metrics.accuracy_score(y, logregpredictions))
print("Confusion matrix: \n", metrics.confusion_matrix(y, logregpredictions))
print("Classification report:\n ", metrics.classification_report(y, logregpredictions))

Accuracy:  0.6600459127657451
Confusion matrix: 
 [[6040 3972]
 [2840 7186]]
Classification report:
               precision    recall  f1-score   support

          0       0.68      0.60      0.64     10012
          1       0.64      0.72      0.68     10026

avg / total       0.66      0.66      0.66     20038



### Discussion
The precision for this model is .68 for predicting 0 and .64 for predicting 1. This shows that this particular model is slightly better at predicting correctly for unsuccessful visas than predicting correctly for successful visa applications. 

The recall for this model has a significant difference between 0 and 1, the recall shows a value of .6 for 0 and a value of .71 for 1, this shows that the model predicts that a visa application will be successful more often than unsuccessful. This is supported by the confusion matrix which shows the combination of positive predictions have approximately 2000 more than the negative predictions. With 4000 of 11000 positive predictions being false positives.

The accuracy of this model is approximately 0.65, although this is not a particularly high value for a predictive model this shows that this model is predicting more correct observations than incorrect observations as it is greater than 0.5. This model appears to be predict more positive outcomes than negative outcomes.

### Evaluate the model using classification evaluation measures on the hold-out (30% examples) test set. Compare these results with the evaluation results obtained when using the training (70%) dataset for evaluation

First we must create dummy variables of the categorical features in the test set.

In [101]:
payUnit_dummies_t = pd.get_dummies(test.pw_unit_of_pay_9089, prefix='Pay')


In [102]:
sourceName_dummies_t = pd.get_dummies(test.pw_source_name_9089, prefix='Source')
sourceName_dummies_t = sourceName_dummies_t.rename(columns=lambda x: x.replace(' ', '_'))


In [103]:
level_dummies_t = pd.get_dummies(test.pw_level_9089, prefix='L')
level_dummies_t = level_dummies_t.rename(columns=lambda x: x.replace(' ', '_'))


In [104]:
region_dummy_t = pd.get_dummies(test.CensusRegion, prefix='CR')
region_dummy_t = region_dummy_t.rename(columns=lambda x: x.replace(' ', '_'))


In [105]:
industry_dummy_t = pd.get_dummies(test.Industry, prefix='l')
industry_dummy_t = industry_dummy_t.rename(columns=lambda x: x.replace(' ', '_'))


In [106]:
test.shape[0]

8578

Below we will add the dummy variables and the test set together into a new dataframe called df_testing.

In [107]:
df_testing = pd.concat([test, industry_dummy_t, region_dummy_t, payUnit_dummies_t, sourceName_dummies_t, level_dummies_t], axis = 1)

df_testing.shape[0]
df_testing.head(5)

case_status country_of_citizenship  decision_date  \
20038   Certified                  INDIA           2015   
20039   Certified                  CHINA           2016   
20040      Denied                  EGYPT           2016   
20041      Denied                  INDIA           2015   
20042      Denied                 MEXICO           2013   

                                employer_name employer_state pw_level_9089  \
20038                          RADIUMSOFT INC        GEORGIA      Level IV   
20039     MANAGEMENT SCIENCE ASSOCIATES, INC.   PENNSYLVANIA      Level II   
20040                       INTEL CORPORATION     CALIFORNIA      Level II   
20041                              TRANSUNION       ILLINOIS      Level II   
20042  FORT WORTH INDEPENDENT SCHOOL DISTRICT          TEXAS           NaN   

                                  pw_soc_title_x pw_source_name_9089  \
20038  Computer and Information Systems Managers                 OES   
20039          Software Developers, Applications                 OES   
20040      Software Developers, Systems Software                 OES   
20041          Software Developers, Applications                 OES   
20042                                        NaN                 NaN   

      pw_unit_of_pay_9089  case_status_code     GDP      GDPGroups country  \
20038                Year                 1  1983.0   Low Rank GDP   INDIA   
20039                Year                 1  8643.0   Mid Rank GDP   CHINA   
20040                Year                 0  2501.0   Mid Rank GDP   EGYPT   
20041                 NaN                 0  1983.0   Low Rank GDP   INDIA   
20042                Year                 0  9304.0  High Rank GDP  MEXICO   

                              advice       Party    Industry  decision_Year  \
20038  2: Exercise increased caution  Republican  Technology           2015   
20039  2: Exercise increased caution  Republican  Technology           2016   
20040  2: Exercise increased caution  Democratic  Technology           2016   
20041  2: Exercise increased caution  Democratic  Technology           2015   
20042  2: Exercise increased caution  Republican       Blank           2013   

       decision_Month        CensusRegion  l_Accounting_and_Finance  l_Blank  \
20038               9      South Atlantic                         0        0   
20039              10     Middle Atlantic                         0        0   
20040               4             Pacific                         0        0   
20041               5  East North Central                         0        0   
20042               1  West South Central                         0        1   

       l_Construction_and_Engineering  l_Education  l_Health_and_Medicine  \
20038                               0            0                      0   
20039                               0            0                      0   
20040                               0            0                      0   
20041                               0            0                      0   
20042                               0            0                      0   

       l_Law  l_Other  l_Sales_and_Marketing  l_Science  l_Technology  \
20038      0        0                      0          0             1   
20039      0        0                      0          0             1   
20040      0        0                      0          0             1   
20041      0        0                      0          0             1   
20042      0        0                      0          0             0   

       CR_East_North_Central  CR_East_South_Central  CR_Middle_Atlantic  \
20038                      0                      0                   0   
20039                      0                      0                   1   
20040                      0                      0                   0   
20041                      1                      0                   0   
20042                      0                   

In [108]:
predict_test_logreg = logreg.predict(df_testing).round()
logreg.predict(df_testing).head()

20038    6.199500e-01
20039    6.917713e-01
20040    6.721754e-01
20041    3.444184e-01
20042    1.801800e-14
dtype: float64

In [109]:
w = test.case_status_code

In [110]:
print("Accuracy: ", metrics.accuracy_score(w, predict_test_logreg))
print("Confusion matrix: \n", metrics.confusion_matrix(w, predict_test_logreg))
print("Classification report:\n ", metrics.classification_report(w, predict_test_logreg))

Accuracy:  0.6646071345301935
Confusion matrix: 
 [[2576 1719]
 [1158 3125]]
Classification report:
               precision    recall  f1-score   support

          0       0.69      0.60      0.64      4295
          1       0.65      0.73      0.68      4283

avg / total       0.67      0.66      0.66      8578



### Discussion
There is a smaller difference between the precision of the model tested on the test set as there is only a difference of .3 between the precision on predicting 0 and predicting 1. Showing that the model appears to be slightly better at predicting positive outcomes correctly in the test dataset.

The precision shows similar trends as it did on the train dataset, showing that the model is overall better at predicting unsuccessful visa applications correctly than successful visa applications. 

The recall for the model tested on the test data set also yields similar results with a recall of .71 for predicting 1 and .61 for predicting 0. 

The accuracy of the model in predicting correct observations is also approximately .65. The similarity in the results of the model tested on the train set and on the test set shows that there is little to no overfitting in this model.

## Testing on the unbalanced data
Below we will test the model trained on the balanced train set on the unbalanced dataframe. We do this so we can compare results to help determine how accurate our model really is.

First we must create dummy variables for the unbalanced dataframe.

In [111]:
payUnit_dummies_t = pd.get_dummies(merged_final_unbal.pw_unit_of_pay_9089, prefix='Pay')

In [112]:
sourceName_dummies_t = pd.get_dummies(merged_final_unbal.pw_source_name_9089, prefix='Source')
sourceName_dummies_t = sourceName_dummies_t.rename(columns=lambda x: x.replace(' ', '_'))

In [113]:
level_dummies_t = pd.get_dummies(merged_final_unbal.pw_level_9089, prefix='L')
level_dummies_t = level_dummies_t.rename(columns=lambda x: x.replace(' ', '_'))

In [114]:
region_dummy_t = pd.get_dummies(merged_final_unbal.CensusRegion, prefix='CR')
region_dummy_t = region_dummy_t.rename(columns=lambda x: x.replace(' ', '_'))

In [115]:
industry_dummy_t = pd.get_dummies(merged_final_unbal.Industry, prefix='l')
industry_dummy_t = industry_dummy_t.rename(columns=lambda x: x.replace(' ', '_'))

In [116]:
merged_final_unbal.shape[0]

153615

To test on the unbalanced dataframe we will create a new dataframe called df_unbal.

In [117]:
df_unbal = pd.concat([merged_final_unbal, industry_dummy_t, region_dummy_t, payUnit_dummies_t, sourceName_dummies_t, level_dummies_t], axis = 1)

df_unbal.shape[0]
df_unbal.head(5)

case_status country_of_citizenship  decision_date             employer_name  \
0   Certified                 TURKEY           2014   APPLIED MATERIALS, INC.   
1      Denied                  INDIA           2015           IBM CORPORATION   
2   Certified                  INDIA           2015         INTEL CORPORATION   
3   Certified                    NaN           2011  ARIZONA STATE UNIVERSITY   
4   Certified                    NaN           2011            QUALCOMM, INC.   

   employer_state pw_level_9089  \
0      CALIFORNIA           NaN   
1  NORTH CAROLINA      Level II   
2      CALIFORNIA           NaN   
3         ARIZONA       Level I   
4      CALIFORNIA      Level II   

                                  pw_soc_title_x pw_source_name_9089  \
0                            Materials Engineers               Other   
1              Software Developers, Applications                 OES   
2         Electronics Engineers, Except Computer               Other   
3       Computer Science Teachers, Postsecondary                 OES   
4  Computer Software Engineers, Systems Software                 OES   

  pw_unit_of_pay_9089  case_status_code      GDP      GDPGroups country  \
0                Year                 1  10512.0  High Rank GDP  TURKEY   
1                Year                 0   1983.0   Low Rank GDP   INDIA   
2                Year                 1   1983.0   Low Rank GDP   INDIA   
3                Year                 1      NaN            NaN     NaN   
4                Year                 1      NaN            NaN     NaN   

                          advice       Party                      Industry  \
0            3:Reconsider travel  Democratic  Construction and Engineering   
1  2: Exercise increased caution  Republican                    Technology   
2  2: Exercise increased caution  Democratic                    Technology   
3                            NaN  Republican                     Education   
4                            NaN  Democratic                    Technology   

   decision_Year  decision_Month    CensusRegion  l_Accounting_and_Finance  \
0           2014               6         Pacific                         0   
1           2015               4  South Atlantic                         0   
2           2015               5         Pacific                         0   
3           2011              12        Mountain                         0   
4           2011              12         Pacific                         0   

   l_Blank  l_Construction_and_Engineering  l_Education  \
0        0                               1            0   
1        0                               0            0   
2        0                               0            0   
3        0                               0            1   
4        0                               0            0   

   l_Health_and_Medicine  l_Law  l_Other  l_Sales_and_Marketing  l_Science  \
0                      0      0        0                      0          0   
1                      0      0        0                      0          0   
2                      0      0        0                      0          0   
3                      0      0        0                      0          0   
4                      0      0        0                      0          0   

   l_Technology  CR_East_North_Central  CR_East_South_Central  \
0             0                      0                      0   
1             1                      0                      0   
2             1                      0                      0   
3             0                      0                      0   
4             1                      0                      0   

   CR_Middle_Atlantic  CR_Mountain  CR_New_England  CR_Pacific  \
0                   0            0               0           1   
1                   0            0               0           0   
2                   0            0               0           1   
3  

In [118]:
predict_test_logreg = logreg.predict(df_unbal).round()
logreg.predict(df_unbal).head()

0    0.595886
1    0.490453
2    0.686349
3    0.133470
4    0.329652
dtype: float64

In [119]:
w = df_unbal.case_status_code
w.shape

(153615,)

In [120]:
print("Accuracy: ", metrics.accuracy_score(w, predict_test_logreg))
print("Confusion matrix: \n", metrics.confusion_matrix(w, predict_test_logreg))
print("Classification report:\n ", metrics.classification_report(w, predict_test_logreg))

Accuracy:  0.7112261172411548
Confusion matrix: 
 [[  8620   5693]
 [ 38667 100635]]
Classification report:
               precision    recall  f1-score   support

          0       0.18      0.60      0.28     14313
          1       0.95      0.72      0.82    139302

avg / total       0.88      0.71      0.77    153615



### Discussion
Interestingly, the values achieved when the model is trained on the balanced data and tested on the unbalanced data are significantly different from the values obtained when the model is tested on balanced dataset.
The model appears to have a very low precision of 0.18 at predicting 0 with a very high precision at predicting 1 of .95. The difference in these values is due to the actual unbalanced data set containing over 90% successful applications. This means that more often than not the applicants in this dataset are successful and so it is less likely the model will predict 1 incorrectly when most of the values in the dataset have a target feature of 1. 

The accuracy of the model tested on the unbalanced set also appears to be 10% higher than the accuracy of the model tested on the other two datasets, this shows that more correct predictions were made on this model. This model trained on the balanced data appears to predict more instances of positive outcomes, which will of course yield better accuracy when tested on a dataset that contains more positive outcomes as the unbalanced one does.

The cross validation shows that there is no overfitting of this model the accuracies against the 10 fold cross validation are very similar.

### Also compare the results of model trained on training set with a cross-validated model

First we must create dummy variables for the whole dataset

In [121]:
payUnit_dummies_cv = pd.get_dummies(merged_final.pw_unit_of_pay_9089, prefix='Pay')


In [122]:
sourceName_dummies_cv = pd.get_dummies(merged_final.pw_source_name_9089, prefix='Source')
sourceName_dummies_cv = sourceName_dummies_cv.rename(columns=lambda x: x.replace(' ', '_'))

In [123]:
level_dummies_cv = pd.get_dummies(merged_final.pw_level_9089, prefix='L')
level_dummies_cv = level_dummies_cv.rename(columns=lambda x: x.replace(' ', '_'))

In [124]:
region_dummy_cv = pd.get_dummies(merged_final.CensusRegion, prefix='CR')
region_dummy_cv = region_dummy_cv.rename(columns=lambda x: x.replace(' ', '_'))

In [125]:
industry_dummy_cv = pd.get_dummies(merged_final.Industry, prefix='l')
industry_dummy_cv = industry_dummy_cv.rename(columns=lambda x: x.replace(' ', '_'))

In [126]:
df_crossV = pd.concat([merged_final, industry_dummy_cv, region_dummy_cv, payUnit_dummies_cv, sourceName_dummies_cv, level_dummies_cv], axis = 1)

df_crossV

case_status    country_of_citizenship  decision_date  \
0          Denied                     INDIA           2015   
1          Denied                     INDIA           2015   
2          Denied                       NaN           2012   
3          Denied                 VENEZUELA           2014   
4          Denied                     INDIA           2013   
5       Certified                     INDIA           2015   
6          Denied                       NaN           2011   
7       Certified                BANGLADESH           2014   
8          Denied                       NaN           2011   
9          Denied                    CANADA           2016   
10      Certified                     NEPAL           2016   
11      Certified                     INDIA           2016   
12         Denied                    TAIWAN           2016   
13      Certified                       NaN           2011   
14         Denied                     INDIA           2013   
15      Certified                     INDIA           2016   
16         Denied               SOUTH KOREA           2014   
17      Certified                    TAIWAN           2016   
18         Denied               PHILIPPINES           2015   
19      Certified                     INDIA           2015   
20      Certified                     INDIA           2016   
21         Denied               SOUTH KOREA           2012   
22      Certified                   GERMANY           2015   
23      Certified                     INDIA           2016   
24      Certified                     INDIA           2016   
25         Denied                     INDIA           2015   
26         Denied                UZBEKISTAN           2014   
27      Certified                     JAPAN           2013   
28         Denied                     CHINA           2016   
29      Certified                     INDIA           2014   
30         Denied                     INDIA           2013   
31      Certified               SOUTH KOREA           2014   
32         Denied                    CANADA           2013   
33      Certified                     INDIA           2014   
34      Certified                     INDIA           2015   
35         Denied            UNITED KINGDOM           2014   
36         Denied                     INDIA           2014   
37         Denied                     INDIA           2016   
38      Certified               PHILIPPINES           2014   
39      Certified                     CHINA           2014   
40         Denied                     INDIA           2016   
41         Denied                     INDIA           2013   
42      Certified                    CANADA           2016   
43      Certified                     INDIA           2016   
44         Denied                       NaN           2012   
45      Certified                     INDIA           2015   
46      Certified                     CHINA           2016   
47      Certified                     INDIA           2013   
48         Denied                    SWEDEN           2016   
49      Certified                     INDIA           2016   
50      Certified                     CHINA           2016   
51         Denied                     INDIA           2016   
52      Certified                    BRAZIL           2016   
53      Certified                     INDIA           2016   
54      Certified                     INDIA           2013   
55      Certified                     INDIA           2016   
56         Denied                     CHINA           2015   
57         Denied                  COLOMBIA           2014   
58      Certified                     INDIA           2014   
59      Certified                     INDIA           2014   
60         Denied                    CANADA           2016   
61         Denied                    CANADA           2016   
62         Denied               PHILIPPINES           2014   
63         Denied                     

In [127]:
l = df_crossV['case_status_code']

In [128]:
df_crossV.shape[0]

28616

In [129]:
intercept = pd.DataFrame({'Intercept': np.ones(28616)})

In [130]:
N = pd.concat([intercept, df_crossV[['decision_date', 'decision_Month', 'CR_Middle_Atlantic', 'CR_East_North_Central', 'CR_Pacific', 'CR_New_England', 'CR_South_Atlantic', 'CR_East_South_Central', 'CR_West_North_Central', 'CR_Mountain', 'CR_West_South_Central', 'Pay_Year', 'Pay_Hour', 'L_Level_I', 'L_Level_II', 'L_Level_III', 'L_Level_IV', 'Source_CBA', 'Source_DBA', 'Source_Employer_Conducted', 'Source_OES', 'Source_Other', 'Source_Other', 'Source_SCA']]], axis=1)

Now we will determine the accuracy of the model using cross validation.

In [131]:
#https://towardsdatascience.com/building-a-logistic-regression-in-python-step-by-step-becd4d56c9c8
X_train1, X_test1, y_train1, y_test1 = train_test_split(N, l, test_size=0.3, random_state=0)
logreg = LogisticRegression()
logreg.fit(X_train1, y_train1)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [132]:
kfold = model_selection.KFold(n_splits=10, random_state=7)
model_CV = LogisticRegression()
scoring = 'accuracy'
results = model_selection.cross_val_score(model_CV, X_train1, y_train1, cv=kfold, scoring=scoring)
print("10-fold cross validation accuracy for each fold: \n", results)
print("10-fold cross validation average accuracy: %.3f" % (results.mean()))

10-fold cross validation accuracy for each fold: 
 [0.60828343 0.62156765 0.58212681 0.61357963 0.60459311 0.60908637
 0.58462307 0.61008487 0.60758862 0.61208188]
10-fold cross validation average accuracy: 0.605


### Discussion
The cross validation done on the whole of the original balanced data set shows an average accuracy of .59, with accuracies ranging from .57 to . 61. The accuracy of the model tested on the test set is .65 as is the accuracy of the model run on the training data set. This is only a 5% difference from the average with some of the cross validated results yielding higher than the average. This would suggest that there is a very minimal amount of overfitting occuring in this model.

## Training a model on the unbalanced dataframe
Below we train a model on the unbalanced data set. We will do this in order to compare the two models so we can see which model is better for the problem at hand of predicting visa applications being either successful or unsuccessful.

In [133]:
train_unbal=df_unbal.sample(frac=0.7,random_state=200)
test_unbal=df_unbal.drop(train_unbal.index)

In [134]:
train_unbal.shape
train_unbal.head(5)

case_status    country_of_citizenship  decision_date  \
114806   Certified                     INDIA           2015   
35146    Certified                     INDIA           2014   
52400    Certified  UNITED STATES OF AMERICA           2013   
13649    Certified                       NaN           2012   
44686    Certified                     INDIA           2014   

                            employer_name employer_state pw_level_9089  \
114806  HALLMARK GLOBAL TECHNOLOGIES INC.       DELAWARE      Level II   
35146                        GEONINE INC.       MICHIGAN      Level IV   
52400        DB SERVICES NEW JERSEY, INC.     NEW JERSEY      Level II   
13649                          GENERAL RE    CONNECTICUT      Level IV   
44686               MICROSOFT CORPORATION     WASHINGTON      Level II   

                           pw_soc_title_x pw_source_name_9089  \
114806  Software Developers, Applications                 OES   
35146   Software Developers, Applications                 OES   
52400        Operations Research Analysts                 OES   
13649            Accountants and Auditors                 OES   
44686   Software Developers, Applications                 OES   

       pw_unit_of_pay_9089  case_status_code     GDP     GDPGroups country  \
114806                Year                 1  1983.0  Low Rank GDP   INDIA   
35146                 Year                 1  1983.0  Low Rank GDP   INDIA   
52400                 Year                 1     NaN           NaN     NaN   
13649                 Year                 1     NaN           NaN     NaN   
44686                 Year                 1  1983.0  Low Rank GDP   INDIA   

                               advice       Party  \
114806  2: Exercise increased caution  Democratic   
35146   2: Exercise increased caution  Republican   
52400                             NaN  Democratic   
13649                             NaN  Democratic   
44686   2: Exercise increased caution  Democratic   

                            Industry  decision_Year  decision_Month  \
114806                    Technology           2015               6   
35146                     Technology           2014               9   
52400   Construction and Engineering           2013               7   
13649         Accounting and Finance           2012               2   
44686                     Technology           2014               7   

              CensusRegion  l_Accounting_and_Finance  l_Blank  \
114806      South Atlantic                         0        0   
35146   East North Central                         0        0   
52400      Middle Atlantic                         0        0   
13649          New England                         1        0   
44686              Pacific                         0        0   

        l_Construction_and_Engineering  l_Education  l_Health_and_Medicine  \
114806                               0            0                      0   
35146                                0            0                      0   
52400                                1            0                      0   
13649                                0            0                      0   
44686                                0            0                      0   

        l_Law  l_Other  l_Sales_and_Marketing  l_Science  l_Technology  \
114806      0        0                      0          0             1   
35146       0        0                      0          0             1   
52400       0        0                      0          0             0   
13649       0        0                      0          0             0   
44686       0        0                      0          0             1   

        CR_East_North_Central  CR_East_South_Central  CR_Middle_Atlantic  \
114806                      0                      0                   0   
35146                       1                      0                   0   
52400                       0               

To test on the unbalanced dataframe we will create a new dataframe called df_unbal.

In [135]:
logreg_unbal_df = sm.logit(formula="case_status_code ~ decision_date + l_Technology + l_Accounting_and_Finance + l_Blank + l_Construction_and_Engineering + l_Education + l_Health_and_Medicine + l_Law + l_Other + l_Sales_and_Marketing + l_Science + decision_Month + CR_Middle_Atlantic + CR_East_North_Central + CR_Pacific + CR_New_England + CR_South_Atlantic + CR_East_South_Central + CR_West_North_Central + CR_Mountain + CR_West_South_Central + Pay_Year + Pay_Hour + L_Level_I + L_Level_II + L_Level_III + L_Level_IV + Source_CBA + Source_Employer_Conducted + Source_OES + Source_Other", data=train_unbal).fit()

print(logreg_unbal_df.params)

Optimization terminated successfully.
         Current function value: 0.272487
         Iterations 9
Intercept                        -624.193579
decision_date                       0.339600
l_Technology                      -61.956104
l_Accounting_and_Finance          -62.022205
l_Blank                           -65.553314
l_Construction_and_Engineering    -61.869526
l_Education                       -62.488088
l_Health_and_Medicine             -61.774538
l_Law                             -61.795962
l_Other                           -62.628478
l_Sales_and_Marketing             -62.280254
l_Science                         -61.825011
decision_Month                      0.049566
CR_Middle_Atlantic                  0.669812
CR_East_North_Central               0.527125
CR_Pacific                          0.842226
CR_New_England                      0.974778
CR_South_Atlantic                   0.335481
CR_East_South_Central               0.790475
CR_West_North_Central               0.93749

In [136]:
predict_unbal_logreg = logreg_unbal_df.predict(train_unbal).round()

In [137]:
K = train_unbal['case_status_code']
K.shape

(107530,)

In [138]:
print("Accuracy: ", metrics.accuracy_score(K, predict_unbal_logreg))
print("Confusion matrix: \n", metrics.confusion_matrix(K, predict_unbal_logreg))
print("Classification report:\n ", metrics.classification_report(K, predict_unbal_logreg))

Accuracy:  0.9153445550079048
Confusion matrix: 
 [[  856  9070]
 [   33 97571]]
Classification report:
               precision    recall  f1-score   support

          0       0.96      0.09      0.16      9926
          1       0.91      1.00      0.96     97604

avg / total       0.92      0.92      0.88    107530



### Discussion
The values achieved from this model appear to be significantly better than the values achieved from the model trained on the balanced dataset.

The accuracy of this model appears to be quite high at approximately 91%. This means this model has a high success rate of predicting the corrrect outcome. 

However the recall value of predicting 0 in this model is extremely low, at approximately 0.08. This means that this model is very poor at frequently predicting an unsuccessful visa application. In the confusion matrix it appears there are much lower numbers of negative predictions in the matrix, however a very small proportion of predictions,  32 are actual false negatives. Meaning our model is not predicting many outcomes as negative incorrectly and there are merely very few negative outcomes in our dataset.

These results align with what we would expect as the model is learning from a dataset containing over 90% of applicants being successful.



## Training and testing on the unbalanced data

To test the accuracy of our model and to detect if there has been any over fitting we will test the model trained on the unbalanced training set on the unbalanced test set.

In [139]:
r = test_unbal['case_status_code']

In [140]:
predict_test_logreg_unbal = logreg_unbal_df.predict(test_unbal).round()
predict_test_logreg_unbal.head()

0    1.0
1    1.0
2    1.0
4    1.0
8    1.0
dtype: float64

In [141]:
print("Accuracy: ", metrics.accuracy_score(r, predict_test_logreg_unbal))
print("Confusion matrix: \n", metrics.confusion_matrix(r, predict_test_logreg_unbal))
print("Classification report:\n ", metrics.classification_report(r, predict_test_logreg_unbal))

Accuracy:  0.9125962894651188
Confusion matrix: 
 [[  379  4008]
 [   20 41678]]
Classification report:
               precision    recall  f1-score   support

          0       0.95      0.09      0.16      4387
          1       0.91      1.00      0.95     41698

avg / total       0.92      0.91      0.88     46085



### Discussion

The values achieved when the model is tested on the test set are in agreement with the values obtained when the model is tested on the train set.

The same trends are seen in the model when it is tested on the test set as when it was tested on the train set. There is a very high accuracy on 91%, with minimal negative predictions being made, and only 19 of the negative predictions are false negatives. The recall score for 0 remains low and much higher at 1 for positives, indicating this model is still predicting much more positive outcomes as can be seen in the confusion matrix.


In [142]:
r = test_unbal['case_status_code']

In [143]:
test_unbal.shape[0]

46085

In [144]:
intercept = pd.DataFrame({'Intercept': np.ones(46085)})
intercept.shape

(46085, 1)

In [145]:
test_unbal = test_unbal.reset_index(drop=True)

In [146]:
T = pd.concat([intercept, test_unbal[['decision_date', 'decision_Month', 'CR_Middle_Atlantic', 'CR_East_North_Central', 'CR_Pacific', 'CR_New_England', 'CR_South_Atlantic', 'CR_East_South_Central', 'CR_West_North_Central', 'CR_Mountain', 'CR_West_South_Central', 'Pay_Year', 'Pay_Hour', 'L_Level_I', 'L_Level_II', 'L_Level_III', 'L_Level_IV', 'Source_CBA', 'Source_DBA', 'Source_Employer_Conducted', 'Source_OES', 'Source_Other', 'Source_Other', 'Source_SCA']]], axis=1)
T.shape

(46085, 25)

Now we will determine the accuracy of the model using cross validation.

In [147]:
#https://towardsdatascience.com/building-a-logistic-regression-in-python-step-by-step-becd4d56c9c8
X_train3, X_test3, y_train3, y_test3 = train_test_split(T, r, test_size=0.3, random_state=0)
logreg_unbal_df  = LogisticRegression()
logreg_unbal_df.fit(X_train3, y_train3)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [148]:
kfold = model_selection.KFold(n_splits=10, random_state=7)
model_CV = LogisticRegression()
scoring = 'accuracy'
results = model_selection.cross_val_score(model_CV, X_train3, y_train3, cv=kfold, scoring=scoring)
print("10-fold cross validation accuracy for each fold: \n", results)
print("10-fold cross validation average accuracy: %.3f" % (results.mean()))

10-fold cross validation accuracy for each fold: 
 [0.92064476 0.91754495 0.90576565 0.9116553  0.90359578 0.91723497
 0.90886547 0.91630502 0.89987601 0.90449612]
10-fold cross validation average accuracy: 0.911


### Discussion

The accuracy of the model on the cross validation performed on the test set appears to be in much greater agreement of the accuracy obtained when the model is tested on the train set. The average accuracy of the cross validation is 91 which is the same as the accuracy achieved when the model is tested on the train dataset. These results suggests over fitting is not occurring in this model.

### Overall Reflection on Models Trained on Balanced Vs Unbalanced

Overall, the model trained on the unbalanced data set appears to yield much better results than the model trained on the balanced dataset. This is subjective however to the dataset the model is being tested on, the model that is trained on the unbalanced dataset will be a better predicter at predicting a successful visa application. Considering this dataset is a real world representation of visa applications in the US and it contains more successful visa applications than unsuccessful visa applications it is possible that a model that predicts more successful applications, as the unbalanced data model, does is the better predicter.